# Maximum occupancy at the trip level

This is the R notebook for the Zero-Inflated Random Forest model.

The following are the required libraries to run the models:

In [3]:
library(randomForest)
library(mlbench)
library(caret)
library(e1071)
library(dplyr)
library(tidyr)
library(tidyverse)
library(readr)
library(ranger)
library(rFerns)
library(ordinalForest)
library(RRF)
library(furrr)

# Maximum occupancy modeling for trips

The `RF_Ferns_and_Rangers2()` performs the zero-inflated random forest model at the trip level. It requires four input values:

* `rt == route_id`
* `di == direction_id`
* `part`: `Pre` or `Post`
* `trip == trip_id`

Also, it has three outputs:

* `Zero_Inf_RF_Chart.csv`: Chart with test data and predictions.
* `Random_Ferns_model.rds`: Trained Random Ferns model for classification.
* `Random_Forest_RANGER_model.rds`: Trained Random Forest (RANGER) model for regression.

In [205]:
RF_Ferns_and_Ranger2 <- function(rt, di, part, trip){
    
    setwd('/home/jmartinez')
    
    library(caret)
    library(ranger)
    
    file_dir = paste('data', 'jmartinez', 'Max_Occupancy_Trips', 'data',
                     sep = '/')
    
    file_name = paste0(part, '_', 'Trips', '_', 'r', rt, '_', 'd', di, '.csv')
    
    file_path = paste(file_dir, file_name, sep = '/')
    
    DF = read_csv(file_path)
        
    trip_df <- DF %>%
        filter(trip_id == trip)
    trip_df <- unique(trip_df)
    
    num_rows_dt = nrow(trip_df)
    
    if(num_rows_dt < 30){
        return('Insufficient data for analysis!')
    }
    else if(num_rows_dt >= 30){
         
        num_zeros = dim(trip_df %>% filter(max_occupancy == 0))[1]
        
        if(num_zeros == 0){
            
            return('There is not zero counts in this dataset, therefore a random forest regression model will be used.')
        }
        else if(num_zeros > 5){
            set.seed(123)
            inTraining <-  createDataPartition(trip_df$max_occupancy,
                                               times = 1, p = 0.7,
                                               list = FALSE)
            DT_train <- trip_df[inTraining, ]
            DT_test <- trip_df[-inTraining, ]

            num_hours = length(unique(trip_df$hour))

            if(num_hours < 2){
                
                col_hour = which(colnames(Pre_Trips_r1_d0) == 'hour', arr.ind = T)

                dt_train = DT_train[ , -c(1:3)]
                dt_test = DT_test[ , -c(1:3)]
            }
            else if(num_hours >= 2){
    
                dt_train = DT_train[, -c(1:2)]
                dt_test = DT_test[, -c(1:2)]
            }

            setwd('data/jmartinez/Max_Occupancy_Trips/Results')
            results_path = paste(paste('route', rt, sep = '_'),
                                 paste(part, 'lockdown', sep = '_'),
                                 paste('direction', di, sep = ''),
                                 sep = '/')
    
            setwd(results_path)
            
            n_row_train = nrow(DT_train)
            
            y_clf_train = dt_train$max_occupancy
            y_clf_train = factor(if_else(y_clf_train == 0, 0, 1))

            y_clf_test = dt_test$max_occupancy
            y_clf_test = factor(if_else(y_clf_test == 0, 0, 1))
            
            Max_Occupancy_train_clf <- data.frame(cbind(y_clf_train, dt_train[, -c(2)]))
            Max_Occupancy_test_clf <- data.frame(cbind(y_clf_test, dt_test[, -c(2)]))
            
           #---------------------------------------------------------------------------------
            # Training characteristics for model tuning:
            #---------------------------------------------------------------------------------

            control <- trainControl(method='cv', 
                                    number = 3, 
                                    search = 'random')

            #---------------------------------------------------------------------------------
            # Classification using Random Ferns:
            #---------------------------------------------------------------------------------

            set.seed(1)
            rf_random <- train(y_clf_train ~ .,
                               data = Max_Occupancy_train_clf,
                               method = 'rFerns',
                               metric = 'Accuracy',
                               tuneLength  = 10, 
                               trControl = control)

             RF_Ferns <- print(rf_random)

             rf_random_pred <- predict(rf_random, newdata = Max_Occupancy_test_clf)

                
             index_for_reg <- which(rf_random_pred == '1', arr.ind = T)
             #---------------------------------------------------------------------------------
             # Regression Model using Ranger:


             set.seed(1)
             rf_reg_ranger <- train(max_occupancy ~ .,
                                    data = (dt_train %>% filter(max_occupancy > 0)),
                                    method = 'ranger',
                                    metric = 'RMSE',
                                    tuneLength  = 10, 
                                    trControl = control)

             RF_Ranger <- print(rf_reg_ranger)

             #----------------------------------------------------------------------------------
             # Validation:
             Max_Occupancy_Test_Val = dt_test
             nrow_test = (1:nrow(dt_test))

             Max_Occupancy_Test_Val$index = nrow_test
             Max_Occupancy_test_reg = Max_Occupancy_Test_Val[index_for_reg, ]
            
             rf_reg_ranger_pred <- predict(rf_reg_ranger, newdata = Max_Occupancy_test_reg)
             Max_Occupancy_test_reg$Ranger_Pred = rf_reg_ranger_pred

             Max_Occupancy_Test_Val = left_join(Max_Occupancy_Test_Val, Max_Occupancy_test_reg, by = 'index')

             Max_Occupancy_Test_Val = Max_Occupancy_Test_Val %>%
                  mutate(RF_Pred = if_else(is.na(Ranger_Pred) == T, 0, Ranger_Pred))

             dt_test$RF_Pred = Max_Occupancy_Test_Val$RF_Pred

             RF_test_RMSE = sqrt(mean((dt_test$max_occupancy - dt_test$RF_Pred)^{2}))
            
             file_path_clf = paste(trip, paste(part, 'lock_RF_Fern.txt', sep = '_'), sep = '/')
            
            file_path_reg = paste(trip, paste(part, 'lock_RF_Reg.txt', sep = '_'), sep = '/')
            file_path_RF_Chart = paste(trip, paste(part, 'Zero_Inf_RF_Chart.csv', sep = '_'), sep = '/')

            final_clf_model = paste(trip, paste(part, 'Random_Ferns_model.rds', sep = '_'), sep = '/')
            final_reg_model = paste(trip, paste(part, 'Random_Forest_RANGER_model.rds', sep = '_'), sep = '/')

            write.table(RF_Ferns, file_path_clf)
            write.table(RF_Ranger, file_path_reg)
            write.csv(dt_test, file_path_RF_Chart)

            saveRDS(rf_random, final_clf_model)
            saveRDS(rf_reg_ranger, final_reg_model)

        }
        
        msg = paste('Done!', trip, 'had', num_zeros, 'in total.')    
        return(msg)
    }
}



In [22]:
#setwd('/home/jmartinez')

Now that we have a function that runs the model for each trip, we could use a `for` loop to iterate this process for all the trips for each combination of `route_id` and `direction_id`:

The following cell shows how to extract the unique `trip_id` values for `route_id == '1'`, `direction_id == '0'`, and pre-lockdown data:

In [29]:
Pre_trip_id_r1_d0 = as.character(unique(Pre_Trips_r1_d0$trip_id))
Pre_trip_id_r1_d0

[1] "132994" "132997" "132998" "133002" "133003" "133004" "133005" "133007"
  [9] "133008" "133009" "133010" "133011" "133013" "133014" "133015" "133018"
 [17] "133024" "133025" "133026" "133028" "133034" "133036" "133038" "132995"
 [25] "133006" "133012" "133016" "133017" "133019" "133020" "133021" "133027"
 [33] "133032" "133033" "133035" "133037" "133001" "133022" "133023" "133029"
 [41] "133031" "133086" "133087" "133089" "133093" "133101" "133104" "133107"
 [49] "133109" "133110" "133112" "133113" "133114" "133115" "133116" "133117"
 [57] "133154" "133156" "133158" "133160" "133162" "132996" "132999" "133000"
 [65] "133030" "133084" "133091" "133095" "133097" "133099" "133100" "133102"
 [73] "133118" "133155" "133157" "133159" "133161" "133163" "133085" "133090"
 [81] "133092" "133094" "133096" "133098" "133105" "133088" "133103" "133108"
 [89] "135825" "135826" "135827" "135828" "135830" "135831" "135832" "135834"
 [97] "135665" "135666" "135667" "135668" "135669" "135671" "135672" "135673"
[105] "135675" "135676" "135677" "135680" "135681" "135683" "135684" "135685"
[113] "135686" "135687" "135688" "135689" "135690" "135691" "135692" "135693"
[121] "135694" "135697" "135699" "135700" "135702" "135703" "135704" "135707"
[129] "135708" "135670" "135679" "135695" "135701" "135705" "135706" "135709"
[137] "135674" "135678" "135696" "135755" "135756" "135757" "135758" "135759"
[145] "135760" "135761" "135763" "135764" "135765" "135766" "135768" "135769"
[153] "135771" "135772" "135773" "135774" "135775" "135776" "135777" "135778"
[161] "135779" "135780" "135781" "135782" "135783" "135784" "135785" "135786"
[169] "135788" "135789" "135833" "135770" "135787" "135829" "135682" "138338"
[177] "138372" "138339" "138341" "138344" "138349" "138351" "138352" "138353"
[185] "138354" "138357" "138358" "138362" "138363" "138368" "138369" "138370"
[193] "138337" "138340" "138342" "138345" "138346" "138347" "138350" "138355"
[201] "138356" "138359" "138360" "138361" "138365" "138366" "138367" "138373"
[209] "138375" "138343" "138374" "138376" "138377" "138378" "138380" "138381"
[217] "138371" "138427" "138429" "138430" "138431" "138434" "138435" "138438"
[225] "138439" "138442" "138443" "138445" "138446" "138447" "138450" "138451"
[233] "138452" "138455" "138457" "138459" "138461" "138497" "138499" "138501"
[241] "138502" "138503" "138504" "138506" "138379" "138428" "138432" "138433"
[249] "138436" "138437" "138440" "138441" "138444" "138448" "138500" "138505"
[257] "138453" "138456" "138458" "138460" "138498"

In [ ]:
# 133002

In [70]:
RF_Ferns_and_Ranger2('1', '0', 'Pre', '133002')


── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done! 133002 had 4 in total."

In [51]:
which(Pre_trip_id_r1_d0 == '133004', arr.ind = T)

[1] 6

In [206]:
for(i in Pre_trip_id_r1_d0[1:length(Pre_trip_id_r1_d0)]){
  print(i)
  RF_Ferns_and_Ranger2('1', '0', 'Pre', i)
  print('Done!')
  print('_*_*_')
}

[1] "132994"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




Random Ferns 

88 samples
 3 predictor
 2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (3 fold) 
Summary of sample sizes: 58, 59, 59 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa     
   1     0.5785441  0.20300560
   2     0.5563218  0.17858558
   3     0.5563218  0.17858558
   7     0.5337165  0.18006271
  11     0.4996169  0.12655493
  13     0.4544061  0.09233819
  14     0.4544061  0.09233819

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

71 samples
 3 predictor

No pre-processing
Resampling: Cross-Validated (3 fold) 
Summary of sample sizes: 48, 48, 46 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE      
   1             1     maxstat     1.213999  0.09542582  1.0142938
   1             3     extratrees  1.471173  0.06416466  1.1890159
   2             1     extratrees  1.212394  0.0


── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "132998"


...

[1] "Done!"
[1] "_*_*_"
[1] "138460"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "138498"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"


In [75]:
Pre_trip_id_r1_d1 = as.character(unique(Pre_Trips_r1_d1$trip_id))
Pre_trip_id_r1_d1

[1] "133039" "133041" "133045" "133046" "133048" "133049" "133050" "133052"
  [9] "133053" "133054" "133055" "133056" "133058" "133059" "133060" "133063"
 [17] "133064" "133069" "133070" "133071" "133073" "133074" "133075" "133076"
 [25] "133078" "133079" "133081" "133083" "133040" "133042" "133047" "133051"
 [33] "133057" "133061" "133062" "133065" "133066" "133067" "133068" "133072"
 [41] "133077" "133080" "133082" "133044" "133123" "133126" "133127" "133129"
 [49] "133134" "133136" "133137" "133140" "133141" "133143" "133145" "133146"
 [57] "133148" "133149" "133150" "133151" "133152" "133153" "133164" "133166"
 [65] "133168" "133170" "133172" "133043" "133120" "133122" "133131" "133133"
 [73] "133135" "133138" "133165" "133167" "133169" "133171" "133173" "133119"
 [81] "133121" "133124" "133125" "133130" "133132" "133128" "133139" "133144"
 [89] "135835" "135836" "135837" "135838" "135839" "135840" "135841" "135842"
 [97] "135843" "135844" "135710" "135711" "135712" "135713" "135714" "135715"
[105] "135716" "135717" "135718" "135719" "135720" "135721" "135722" "135723"
[113] "135724" "135725" "135726" "135728" "135729" "135730" "135731" "135732"
[121] "135733" "135734" "135735" "135736" "135737" "135738" "135740" "135742"
[129] "135743" "135746" "135747" "135749" "135750" "135751" "135752" "135753"
[137] "135744" "135745" "135748" "135754" "135741" "135790" "135791" "135792"
[145] "135793" "135794" "135795" "135797" "135798" "135799" "135800" "135802"
[153] "135803" "135804" "135805" "135806" "135807" "135808" "135809" "135810"
[161] "135811" "135812" "135813" "135814" "135815" "135816" "135818" "135819"
[169] "135820" "135821" "135822" "135823" "135824" "135817" "135727" "138383"
[177] "138417" "138384" "138385" "138387" "138390" "138392" "138393" "138394"
[185] "138398" "138399" "138402" "138403" "138407" "138408" "138413" "138414"
[193] "138415" "138382" "138388" "138389" "138391" "138395" "138396" "138400"
[201] "138401" "138404" "138405" "138406" "138410" "138411" "138412" "138418"
[209] "138420" "138386" "138416" "138419" "138421" "138422" "138423" "138424"
[217] "138426" "138425" "138463" "138464" "138465" "138469" "138470" "138474"
[225] "138475" "138476" "138478" "138481" "138482" "138483" "138484" "138486"
[233] "138487" "138488" "138491" "138493" "138495" "138507" "138509" "138511"
[241] "138512" "138513" "138514" "138515" "138516" "138462" "138466" "138467"
[249] "138468" "138471" "138472" "138473" "138477" "138510" "138480" "138489"
[257] "138492" "138494" "138496" "138508"

In [207]:
for(i in Pre_trip_id_r1_d1[1:length(Pre_trip_id_r1_d1)]){
  print(i)
  RF_Ferns_and_Ranger2('1', '1', 'Pre', i)
  print('Done!')
  print('_*_*_')
}

[1] "133039"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "133041"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "133045"


...

[1] "Done!"
[1] "_*_*_"
[1] "138496"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "138508"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"


In [208]:
Pre_trip_id_r4_d0 = as.character(unique(Pre_Trips_r4_d0$trip_id))
Pre_trip_id_r4_d0

[1] "134296" "134298" "134299" "134300" "134302" "134303" "134304" "134305"
  [9] "134306" "134307" "134309" "134310" "134311" "134312" "134313" "134314"
 [17] "134315" "134316" "134317" "134318" "134319" "134322" "134323" "134326"
 [25] "134327" "134328" "134329" "134330" "134332" "134333" "134335" "134336"
 [33] "134337" "134338" "134341" "134344" "134345" "134346" "134347" "134348"
 [41] "134349" "134350" "134351" "134354" "134355" "134356" "134357" "134360"
 [49] "134361" "134362" "134301" "134320" "134324" "134325" "134334" "134339"
 [57] "134340" "134342" "134343" "134352" "134353" "134358" "134359" "134363"
 [65] "134297" "134308" "134321" "134331" "134432" "134434" "134436" "134438"
 [73] "134440" "134441" "134443" "134444" "134445" "134446" "134448" "134449"
 [81] "134450" "134452" "134455" "134457" "134460" "134461" "134462" "134463"
 [89] "134465" "134466" "134467" "134468" "134469" "134470" "134471" "134472"
 [97] "134514" "134515" "134516" "134517" "134521" "134522" "134524" "134433"
[105] "134435" "134437" "134439" "134442" "134451" "134453" "134454" "134464"
[113] "134523" "134447" "134456" "134458" "134459" "134518" "134519" "134520"
[121] "137188" "137189" "137190" "137191" "137192" "137193" "137194" "137195"
[129] "137196" "137197" "137198" "136970" "136971" "136972" "136974" "136975"
[137] "136976" "136977" "136978" "136980" "136981" "136982" "136983" "136984"
[145] "136985" "136988" "136989" "136992" "136995" "136996" "136997" "136998"
[153] "136999" "137001" "137002" "137003" "137004" "137005" "137006" "137008"
[161] "137011" "137014" "137015" "137016" "137017" "137019" "137021" "137022"
[169] "137023" "137024" "137025" "137026" "137028" "137029" "137030" "137031"
[177] "137032" "137034" "137035" "137036" "137037" "136973" "136979" "136986"
[185] "136987" "136990" "136991" "136993" "136994" "137009" "137020" "137027"
[193] "137033" "137106" "137107" "137108" "137109" "137110" "137111" "137112"
[201] "137113" "137114" "137115" "137116" "137117" "137118" "137119" "137120"
[209] "137121" "137122" "137123" "137124" "137125" "137126" "137127" "137128"
[217] "137129" "137131" "137132" "137133" "137134" "137135" "137136" "137137"
[225] "137139" "137141" "137142" "137143" "137144" "137145" "137146" "137130"
[233] "137138" "137140" "139636" "139637" "139639" "139642" "139647" "139651"
[241] "139652" "139653" "139655" "139657" "139658" "139659" "139660" "139661"
[249] "139662" "139663" "139664" "139665" "139666" "139667" "139668" "139669"
[257] "139670" "139671" "139675" "139678" "139679" "139680" "139681" "139685"
[265] "139686" "139687" "139688" "139689" "139690" "139692" "139693" "139694"
[273] "139695" "139696" "139640" "139643" "139644" "139646" "139649" "139650"
[281] "139656" "139682" "139691" "139697" "139638" "139645" "139654" "139672"
[289] "139673" "139674" "139676" "139677" "139683" "139684" "139641" "139648"
[297] "139761" "139763" "139764" "139766" "139768" "139770" "139775" "139776"
[305] "139777" "139779" "139782" "139783" "139784" "139786" "139787" "139788"
[313] "139789" "139791" "139793" "139794" "139795" "139796" "139843" "139845"
[321] "139846" "139848" "139849" "139850" "139852" "139762" "139765" "139767"
[329] "139769" "139772" "139774" "139778" "139780" "139781" "139792" "139797"
[337] "139798" "139800" "139842" "139844" "139847" "139851" "139790" "139799"
[345] "139760" "139771" "139773" "139785"

In [209]:
for(i in Pre_trip_id_r4_d0[1:length(Pre_trip_id_r4_d0)]){
  print(i)
  RF_Ferns_and_Ranger2('4', '0', 'Pre', i)
  print('Done!')
  print('_*_*_')
}

[1] "134296"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




Random Ferns 

102 samples
  3 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (3 fold) 
Summary of sample sizes: 69, 68, 67 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.8820219  0.7606171
   2     0.8820219  0.7606171
   3     0.8820219  0.7606171
   7     0.8820219  0.7606171
  11     0.8820219  0.7606171
  13     0.8820219  0.7606171
  14     0.8820219  0.7606171

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

59 samples
 3 predictor

No pre-processing
Resampling: Cross-Validated (3 fold) 
Summary of sample sizes: 40, 40, 38 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared   MAE     
   1             1     maxstat     1.477598  0.2457134  1.242052
   1             3     extratrees  1.391667  0.2868762  1.102346
   2             1     extratrees  1.449997  0.2017109  1.1


── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "134299"


...

[1] "Done!"
[1] "_*_*_"
[1] "139773"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "139785"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"


In [84]:
Pre_trip_id_r4_d1 = as.character(unique(Pre_Trips_r4_d1$trip_id))
Pre_trip_id_r4_d1

[1] "134364" "134365" "134366" "134368" "134370" "134371" "134372" "134373"
  [9] "134374" "134375" "134376" "134378" "134379" "134380" "134382" "134383"
 [17] "134384" "134385" "134386" "134387" "134388" "134390" "134392" "134393"
 [25] "134394" "134397" "134398" "134399" "134400" "134401" "134403" "134404"
 [33] "134406" "134407" "134408" "134409" "134410" "134415" "134416" "134417"
 [41] "134418" "134420" "134421" "134422" "134425" "134426" "134427" "134428"
 [49] "134369" "134377" "134389" "134391" "134395" "134396" "134405" "134411"
 [57] "134412" "134413" "134414" "134423" "134424" "134429" "134431" "134367"
 [65] "134381" "134402" "134419" "134430" "134473" "134475" "134477" "134479"
 [73] "134482" "134483" "134485" "134486" "134487" "134488" "134490" "134491"
 [81] "134492" "134494" "134495" "134498" "134500" "134503" "134504" "134505"
 [89] "134508" "134509" "134510" "134511" "134512" "134513" "134525" "134526"
 [97] "134528" "134529" "134532" "134533" "134535" "134474" "134476" "134478"
[105] "134480" "134484" "134493" "134496" "134497" "134507" "134534" "134489"
[113] "134499" "134501" "134502" "134506" "134530" "134481" "134527" "134531"
[121] "137199" "137200" "137201" "137202" "137203" "137204" "137205" "137206"
[129] "137207" "137208" "137209" "137038" "137039" "137040" "137041" "137042"
[137] "137043" "137044" "137046" "137047" "137048" "137049" "137050" "137054"
[145] "137059" "137060" "137061" "137062" "137063" "137064" "137066" "137067"
[153] "137068" "137069" "137070" "137071" "137073" "137076" "137077" "137079"
[161] "137080" "137081" "137082" "137085" "137086" "137087" "137088" "137089"
[169] "137090" "137091" "137092" "137094" "137095" "137096" "137097" "137098"
[177] "137099" "137100" "137101" "137104" "137105" "137051" "137052" "137053"
[185] "137055" "137056" "137057" "137058" "137074" "137084" "137093" "137103"
[193] "137045" "137147" "137148" "137149" "137150" "137151" "137152" "137153"
[201] "137154" "137155" "137157" "137158" "137159" "137160" "137161" "137162"
[209] "137163" "137164" "137165" "137166" "137167" "137168" "137169" "137170"
[217] "137171" "137172" "137173" "137174" "137175" "137176" "137177" "137178"
[225] "137180" "137182" "137183" "137184" "137185" "137186" "137187" "137156"
[233] "137179" "137181" "139698" "139704" "139705" "139711" "139713" "139714"
[241] "139715" "139716" "139717" "139718" "139719" "139721" "139722" "139723"
[249] "139724" "139725" "139726" "139727" "139728" "139729" "139730" "139731"
[257] "139732" "139733" "139734" "139735" "139736" "139737" "139743" "139744"
[265] "139745" "139746" "139750" "139751" "139752" "139753" "139754" "139755"
[273] "139757" "139758" "139700" "139703" "139706" "139707" "139709" "139712"
[281] "139720" "139747" "139756" "139759" "139699" "139701" "139708" "139738"
[289] "139739" "139740" "139741" "139742" "139748" "139749" "139702" "139710"
[297] "139802" "139804" "139805" "139807" "139809" "139810" "139812" "139817"
[305] "139818" "139819" "139821" "139825" "139826" "139827" "139829" "139830"
[313] "139831" "139834" "139836" "139837" "139838" "139854" "139857" "139858"
[321] "139859" "139860" "139861" "139863" "139803" "139806" "139808" "139811"
[329] "139814" "139816" "139820" "139822" "139824" "139832" "139835" "139839"
[337] "139840" "139841" "139853" "139855" "139856" "139862" "139823" "139833"
[345] "139801" "139813" "139815" "139828"

In [85]:
for(i in Pre_trip_id_r4_d1[1:length(Pre_trip_id_r4_d1)]){
  print(i)
  RF_Ferns_and_Ranger2('4', '1', 'Pre', i)
  print('Done!')
  print('_*_*_')
}

[1] "134364"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "134365"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "134366"


...

[1] "Done!"
[1] "_*_*_"
[1] "139815"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "139828"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"


In [210]:
Pre_trip_id_r9_d0 = as.character(unique(Pre_Trips_r9_d0$trip_id))
Pre_trip_id_r9_d0

[1] "134767" "134768" "134769" "134770" "134771" "134772" "134773" "134774"
  [9] "134777" "134778" "134780" "134781" "134782" "134783" "134786" "134787"
 [17] "134788" "134789" "134793" "134794" "134795" "134779" "134775" "134776"
 [25] "134784" "134785" "134825" "134826" "134827" "134828" "134829" "134830"
 [33] "134831" "134832" "134833" "134834" "134835" "134836" "134837" "134838"
 [41] "134839" "134841" "134842" "134844" "134867" "134868" "134869" "134870"
 [49] "134871" "134872" "134873" "134874" "134875" "134840" "134843" "134845"
 [57] "134790" "134791" "134792" "137551" "137554" "137555" "137557" "137558"
 [65] "137559" "137451" "137452" "137453" "137454" "137455" "137456" "137457"
 [73] "137458" "137459" "137460" "137461" "137462" "137463" "137464" "137465"
 [81] "137466" "137467" "137468" "137469" "137470" "137471" "137472" "137473"
 [89] "137474" "137475" "137476" "137477" "137478" "137479" "137510" "137511"
 [97] "137513" "137514" "137516" "137517" "137518" "137520" "137521" "137523"
[105] "137524" "137525" "137526" "137527" "137528" "137529" "137552" "137553"
[113] "137556" "137512" "137515" "137519" "137522" "140105" "140106" "140103"
[121] "140098" "140099" "140102" "140110" "140111" "140112" "140113" "140117"
[129] "140120" "140121" "140122" "140124" "140125" "140097" "140100" "140101"
[137] "140104" "140107" "140108" "140109" "140116" "140118" "140119" "140123"
[145] "140114" "140115" "140155" "140158" "140160" "140161" "140163" "140164"
[153] "140166" "140167" "140168" "140169" "140170" "140172" "140173" "140174"
[161] "140197" "140198" "140199" "140200" "140201" "140202" "140203" "140204"
[169] "140205" "140162" "140165" "140171" "140156" "140157" "140159"

In [211]:
for(i in Pre_trip_id_r9_d0[1:length(Pre_trip_id_r9_d0)]){
  print(i)
  RF_Ferns_and_Ranger2('9', '0', 'Pre', i)
  print('Done!')
  print('_*_*_')
}

[1] "134767"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




Random Ferns 

103 samples
  3 predictor
  2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (3 fold) 
Summary of sample sizes: 68, 70, 68 
Resampling results across tuning parameters:

  depth  Accuracy   Kappa    
   1     0.6704185  0.3476773
   2     0.6704185  0.3476773
   3     0.6704185  0.3476773
   7     0.6704185  0.3476773
  11     0.6704185  0.3476773
  13     0.6608947  0.3324308
  14     0.6608947  0.3324308

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

68 samples
 3 predictor

No pre-processing
Resampling: Cross-Validated (3 fold) 
Summary of sample sizes: 45, 46, 45 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared    MAE     
   1             1     maxstat     1.415932  0.09897887  1.046237
   1             3     extratrees  1.625810  0.03104554  1.210166
   2             1     extratrees  1.452311  0.07643065 


── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




Random Ferns 

92 samples
 3 predictor
 2 classes: '0', '1' 

No pre-processing
Resampling: Cross-Validated (3 fold) 
Summary of sample sizes: 61, 61, 62 
Resampling results across tuning parameters:

  depth  Accuracy    Kappa     
   1     0.38172043  0.06909716
   2     0.38100358  0.06328917
   3     0.34838710  0.05504099
   7     0.14157706  0.01166837
  11     0.06523297  0.00000000
  13     0.06523297  0.00000000
  14     0.06523297  0.00000000

Accuracy was used to select the optimal model using the largest value.
The final value used for the model was depth = 1.
Random Forest 

86 samples
 3 predictor

No pre-processing
Resampling: Cross-Validated (3 fold) 
Summary of sample sizes: 59, 58, 55 
Resampling results across tuning parameters:

  min.node.size  mtry  splitrule   RMSE      Rsquared   MAE     
   1             1     maxstat     2.144076  0.1460116  1.727079
   1             3     extratrees  2.003385  0.2819562  1.570695
   2             1     extratrees  2.085438  0

...

[1] "Done!"
[1] "_*_*_"
[1] "140157"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "140159"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"


In [212]:
Pre_trip_id_r9_d1 = as.character(unique(Pre_Trips_r9_d1$trip_id))
Pre_trip_id_r9_d1

[1] "134796" "134797" "134798" "134799" "134800" "134801" "134802" "134803"
  [9] "134804" "134807" "134808" "134810" "134811" "134812" "134813" "134816"
 [17] "134817" "134818" "134819" "134823" "134824" "134809" "134805" "134806"
 [25] "134814" "134815" "134846" "134847" "134848" "134849" "134850" "134851"
 [33] "134852" "134853" "134854" "134855" "134856" "134857" "134858" "134859"
 [41] "134860" "134862" "134863" "134865" "134876" "134877" "134878" "134879"
 [49] "134880" "134881" "134882" "134883" "134884" "134861" "134864" "134866"
 [57] "134820" "134821" "134822" "137560" "137563" "137564" "137566" "137567"
 [65] "137568" "137480" "137481" "137482" "137483" "137484" "137485" "137486"
 [73] "137487" "137488" "137489" "137490" "137491" "137492" "137493" "137494"
 [81] "137495" "137496" "137497" "137498" "137499" "137500" "137501" "137502"
 [89] "137503" "137504" "137505" "137506" "137507" "137508" "137531" "137532"
 [97] "137534" "137535" "137536" "137537" "137538" "137539" "137541" "137542"
[105] "137545" "137546" "137547" "137548" "137549" "137550" "137561" "137562"
[113] "137565" "137533" "137540" "137543" "137544" "140135" "140136" "140129"
[121] "140127" "140128" "140132" "140140" "140141" "140142" "140143" "140147"
[129] "140150" "140151" "140152" "140153" "140154" "140126" "140130" "140131"
[137] "140133" "140134" "140137" "140138" "140139" "140146" "140148" "140149"
[145] "140144" "140145" "140176" "140179" "140180" "140181" "140183" "140185"
[153] "140187" "140188" "140189" "140190" "140191" "140193" "140194" "140195"
[161] "140206" "140207" "140208" "140209" "140210" "140211" "140212" "140213"
[169] "140214" "140182" "140186" "140192" "140177" "140178" "140184"

In [213]:
for(i in Pre_trip_id_r9_d1[1:length(Pre_trip_id_r9_d1)]){
  print(i)
  RF_Ferns_and_Ranger2('9', '1', 'Pre', i)
  print('Done!')
  print('_*_*_')
}

[1] "134796"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "134797"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "134798"


...

[1] "Done!"
[1] "_*_*_"
[1] "140178"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"
[1] "140184"



── Column specification ────────────────────────────────────────────────────────
cols(
  trip_date = col_date(format = ""),
  trip_id = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double()
)




[1] "Done!"
[1] "_*_*_"


In [92]:
setwd('/home/jmartinez')

# Aggregate trip performance

The following function aggregates the RMSE values that characterize the trip performance of the models:

In [174]:
aggregate_trips <- function(rt, di){
    
    setwd('/home/jmartinez')
    
    main_dir = paste('data', 'jmartinez', 'Max_Occupancy_Trips', 'Results', paste('route', rt, sep = '_'),
                     'Pre_lockdown', paste('direction', di, sep = ''), sep = '/')
    
    setwd(main_dir)
    
    folder_list = list.files()
    
    train_RMSE_Poiss = test_RMSE_Poiss = c()
    train_RMSE_NB = test_RMSE_NB = c()
    train_RMSE_ZIP = test_RMSE_ZIP = c()
    train_RMSE_ZINB = test_RMSE_ZINB = c()
    train_RMSE_Hurdle = test_RMSE_Hurdle = c()
    train_RMSE_RF = test_RMSE_RF = c()
    test_RMSE_Zero_Inf_RF = c()
    
    for(i in folder_list){
        setwd('/home/jmartinez')
        
        temp_dir = i
    
        main_dir = paste('data', 'jmartinez', 'Max_Occupancy_Trips', 'Results', paste('route', rt, sep = '_'),
                         'Pre_lockdown', paste('direction', di, sep = ''), temp_dir, sep = '/')
        
        setwd(main_dir)
        
        print(temp_dir)
        
        file_list = list.files()
        if(length(file_list) == 0){
            
            train_RMSE_Poiss[i] = test_RMSE_Poiss[i] = NA
            train_RMSE_NB[i] = test_RMSE_NB[i] = NA
            train_RMSE_ZIP[i] = test_RMSE_ZIP[i] = NA
            train_RMSE_ZINB[i] = test_RMSE_ZINB[i] = NA
            train_RMSE_Hurdle[i] = test_RMSE_Hurdle[i] = NA
            train_RMSE_RF[i] = test_RMSE_RF[i] = NA
            test_RMSE_Zero_Inf_RF[i] = NA
        }
        else if(length(file_list) > 0){
            
            glm_exits = grep('Pre_RMSEs.csv', file_list)
            RF_exits = grep('Pre_RF_RMSEs.csv', file_list)
            ZeroInf_RF_exits = grep('Pre_Zero_Inf_RF_RMSEs.csv', file_list)
            
            if(length(glm_exits) == 1){
            
                Pre_RMSEs = read_csv('Pre_RMSEs.csv')

                if(dim(Pre_RMSEs)[2] <= 3){

                    print('This trip did have enough data for meodeling')

                    train_RMSE_Poiss[i] = test_RMSE_Poiss[i] = NA
                    train_RMSE_NB[i] = test_RMSE_NB[i] = NA
                    train_RMSE_ZIP[i] = test_RMSE_ZIP[i] = NA
                    train_RMSE_ZINB[i] = test_RMSE_ZINB[i] = NA
                    train_RMSE_Hurdle[i] = test_RMSE_Hurdle[i] = NA
                    train_RMSE_RF[i] = test_RMSE_RF[i] = NA
                    test_RMSE_Zero_Inf_RF[i] = NA
                }
                else{

                    Pre_RF_RMSEs = read_csv('Pre_RF_RMSEs.csv')

                    train_RMSE_Poiss[i] = Pre_RMSEs$Poiss_RMSE[1]
                    train_RMSE_NB[i] = Pre_RMSEs$NB_RMSE[1]
                    train_RMSE_ZIP[i] = Pre_RMSEs$ZIP_RMSE[1]
                    train_RMSE_ZINB[i] = Pre_RMSEs$ZINB_RMSE[1]
                    train_RMSE_Hurdle[i] = Pre_RMSEs$Hurdle_RMSE[1]
                    train_RMSE_RF[i] = Pre_RF_RMSEs$Train[1]

                    test_RMSE_Poiss[i] = Pre_RMSEs$Poiss_RMSE[2]
                    test_RMSE_NB[i] = Pre_RMSEs$NB_RMSE[2]
                    test_RMSE_ZIP[i] = Pre_RMSEs$ZIP_RMSE[2]
                    test_RMSE_ZINB[i] = Pre_RMSEs$ZINB_RMSE[2]
                    test_RMSE_Hurdle[i] = Pre_RMSEs$Hurdle_RMSE[2]
                    test_RMSE_RF[i] = Pre_RF_RMSEs$Test[2]

                    if(length(ZeroInf_RF_exits) == 1){

                        Pre_Zero_Inf_RF_Chart = read_csv('Pre_Zero_Inf_RF_RMSEs.csv')
                        Pre_Zero_Inf_RF_test_RMSE = sqrt(mean((Pre_Zero_Inf_RF_Chart$max_occupancy - Pre_Zero_Inf_RF_Chart$RF_Pred)^{2}))

                        test_RMSE_Zero_Inf_RF[i] = Pre_Zero_Inf_RF_test_RMSE

                    }
                    else{

                        test_RMSE_Zero_Inf_RF[i] = NA
                    }
                }
            
            }
            else{
                if(length(RF_exits) == 1 ){

                    Pre_RF_RMSEs = read_csv('Pre_RF_RMSEs.csv')

                    if(length(ZeroInf_RF_exits) == 1){

                        Pre_Zero_Inf_RF_Chart = read_csv('Pre_Zero_Inf_RF_RMSEs.csv')
                        Pre_Zero_Inf_RF_test_RMSE = sqrt(mean((Pre_Zero_Inf_RF_Chart$max_occupancy - Pre_Zero_Inf_RF_Chart$RF_Pred)^{2}))
                        
                        train_RMSE_Poiss[i] = NA
                        train_RMSE_NB[i] = NA
                        train_RMSE_ZIP[i] = NA
                        train_RMSE_ZINB[i] = NA
                        train_RMSE_Hurdle[i] = NA
                        train_RMSE_RF[i] = Pre_RF_RMSEs$Train[1]
                        
                        test_RMSE_Poiss[i] = NA
                        test_RMSE_NB[i] = NA
                        test_RMSE_ZIP[i] = NA
                        test_RMSE_ZINB[i] = NA
                        test_RMSE_Hurdle[i] = NA
                        test_RMSE_RF[i] = Pre_RF_RMSEs$Test[2]

                        test_RMSE_Zero_Inf_RF[i] = Pre_Zero_Inf_RF_test_RMSE

                    }
                    else{

                        test_RMSE_Zero_Inf_RF[i] = NA
                    }
                }
                else{
                    
                    train_RMSE_Poiss[i] = test_RMSE_Poiss[i] = NA
                    train_RMSE_NB[i] = test_RMSE_NB[i] = NA
                    train_RMSE_ZIP[i] = test_RMSE_ZIP[i] = NA
                    train_RMSE_ZINB[i] = test_RMSE_ZINB[i] = NA
                    train_RMSE_Hurdle[i] = test_RMSE_Hurdle[i] = NA
                    train_RMSE_RF[i] = test_RMSE_RF[i] = NA
                    test_RMSE_Zero_Inf_RF[i] = NA
                }
            }    
        }
    }
    
    
    setwd('/home/jmartinez')
    
    Trip_Train_RMSE_Performance = data.frame(cbind(
        'Poiss' = train_RMSE_Poiss,
        'NB' = train_RMSE_NB,
        'ZIP' = train_RMSE_ZIP,
        'ZINB' = train_RMSE_ZINB,
        'Hurdle' = train_RMSE_Hurdle,
        'RF' = train_RMSE_RF
    ))
    
    Trip_Test_RMSE_Performance = data.frame(cbind(
        'Poiss' = test_RMSE_Poiss,
        'NB' = test_RMSE_NB,
        'ZIP' = test_RMSE_ZIP,
        'ZINB' = test_RMSE_ZINB,
        'Hurdle' = test_RMSE_Hurdle,
        'RF' = test_RMSE_RF,
        'Zero_Inf_RF' = test_RMSE_Zero_Inf_RF
    ))
    
    return(Trip_Test_RMSE_Performance)
    
    write.csv(Trip_Train_RMSE_Performance, paste0('route', '_', rt, '_', 'direction', di, Trip_Train_RMSE_Performance, '.csv'))
    write.csv(Test_Test_RMSE_Performance, paste0('route', '_', rt, '_', 'direction', di, Trip_Test_RMSE_Performance, '.csv'))
    

}

In [192]:
aggregate_trips2 <- function(rt, di){
    
    setwd('/home/jmartinez')
    
    main_dir = paste('data', 'jmartinez', 'Max_Occupancy_Trips', 'Results', paste('route', rt, sep = '_'),
                     'Pre_lockdown', paste('direction', di, sep = ''), sep = '/')
    
    setwd(main_dir)
    
    folder_list = list.files()
    
    train_RMSE_RF = test_RMSE_RF = c()
    test_RMSE_Zero_Inf_RF = c()
    
    for(i in folder_list){
        setwd('/home/jmartinez')
        
        temp_dir = i
    
        main_dir = paste('data', 'jmartinez', 'Max_Occupancy_Trips', 'Results', paste('route', rt, sep = '_'),
                         'Pre_lockdown', paste('direction', di, sep = ''), temp_dir, sep = '/')
        
        setwd(main_dir)
        
        print(temp_dir)
        
        file_list = list.files()
        
        
        if(length(file_list) == 0){
            
            train_RMSE_RF[i] = test_RMSE_RF[i] = NA
            test_RMSE_Zero_Inf_RF[i] = NA
        }
        else if(length(file_list) > 0){
            
            RF_exits = grep('Pre_RF_RMSEs.csv', file_list)
            ZeroInf_RF_exits = grep('Pre_Zero_Inf_RF_Chart.csv', file_list)
            
            if(length(RF_exits) == 1){

                if(length(ZeroInf_RF_exits) == 1){
                    
                    Pre_RF_RMSEs = read_csv('Pre_RF_RMSEs.csv')
                    Pre_Zero_Inf_RF_Chart = read_csv('Pre_Zero_Inf_RF_Chart.csv')
                    Pre_Zero_Inf_RF_test_RMSE = sqrt(mean((Pre_Zero_Inf_RF_Chart$max_occupancy - Pre_Zero_Inf_RF_Chart$RF_Pred)^{2}))
                    
                    train_RMSE_RF[i] = Pre_RF_RMSEs$Train[1]
                    test_RMSE_RF[i] = Pre_RF_RMSEs$Test[1]
                    
                    test_RMSE_Zero_Inf_RF[i] = Pre_Zero_Inf_RF_test_RMSE
                    
                    
                }
                else if(length(ZeroInf_RF_exits) == 0){
                    
                    Pre_RF_RMSEs = read_csv('Pre_RF_RMSEs.csv')
                    #Pre_Zero_Inf_RF_Chart = read_csv('Pre_Zero_Inf_RF_RMSEs.csv')
                    #Pre_Zero_Inf_RF_test_RMSE = sqrt(mean((Pre_Zero_Inf_RF_Chart$max_occupancy - Pre_Zero_Inf_RF_Chart$RF_Pred)^{2}))
                    
                    train_RMSE_RF[i] = Pre_RF_RMSEs$Train[1]
                    test_RMSE_RF[i] = Pre_RF_RMSEs$Test[1]
                    
                    test_RMSE_Zero_Inf_RF[i] = NA

                }
            }
            else if(length(RF_exits) == 0){
                
                if(length(RF_exits) == 1){
                    

                   Pre_Zero_Inf_RF_Chart = read_csv('Pre_Zero_Inf_RF_Chart.csv')
                   Pre_Zero_Inf_RF_test_RMSE = sqrt(mean((Pre_Zero_Inf_RF_Chart$max_occupancy - Pre_Zero_Inf_RF_Chart$RF_Pred)^{2}))
                    
                   train_RMSE_RF[i] = NA
                   test_RMSE_RF[i] = NA
                   test_RMSE_Zero_Inf_RF[i] = Pre_Zero_Inf_RF_test_RMSE

                }
                else if(length(RF_exits) == 0){
                    
                    train_RMSE_RF[i] = NA
                    test_RMSE_RF[i] = NA
                    test_RMSE_Zero_Inf_RF[i] = NA
                }
            }
            
        }    
    }
    
    
    setwd('/home/jmartinez')
    
    Trip_Train_RMSE_Performance = data.frame(cbind(
        'RF' = train_RMSE_RF
    ))
    
    Trip_Test_RMSE_Performance = data.frame(cbind(
        'RF' = test_RMSE_RF,
        'Zero_Inf_RF' = test_RMSE_Zero_Inf_RF
    ))
    
    return(Trip_Test_RMSE_Performance)
    
    write.csv(Trip_Train_RMSE_Performance, paste0('route', '_', rt, '_', 'direction', di, Trip_Train_RMSE_Performance, '.csv'))
    write.csv(Test_Test_RMSE_Performance, paste0('route', '_', rt, '_', 'direction', di, Trip_Test_RMSE_Performance, '.csv'))
    

}

In [164]:
setwd('/home/jmartinez/')

In [169]:
The following cell aggregates the RMSE values in one data frame 

[1] "route_rt_directiondi_Trip_Train_RMSE_Performance.csv"

In [214]:
trips_RMSE_r1_d02 = aggregate_trips2('1', '0')
trips_RMSE_r1_d02

[1] "132994"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "132995"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "132996"


...

Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "138427"
[1] "138428"
[1] "138429"
[1] "138430"
[1] "138431"
[1] "138432"
[1] "138433"
[1] "138434"
[1] "138435"
[1] "138436"
[1] "138437"
[1] "138438"
[1] "138439"
[1] "138440"
[1] "138441"
[1] "138442"
[1] "138443"
[1] "138444"
[1] "138445"
[1] "138446"
[1] "138447"
[1] "138448"
[1] "138450"
[1] "138451"
[1] "138452"
[1] "138453"
[1] "138455"
[1] "138456"
[1] "138457"
[1] "138458"
[1] "138459"
[1] "138460"
[1] "138461"
[1] "138497"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "138498"
[1] "138499"
[1] "138500"
[1] "138501"
[1] "138502"
[1] "138503"
[1] "138504"
[1] "138505"
[1] "138506"


RF        Zero_Inf_RF
132994 1.1736624 1.1154603  
132995 0.7422244 0.5210501  
132996 2.5287334        NA  
132997 3.2488900        NA  
132998 1.4017994 1.3268382  
132999 3.0204008        NA  
133000 1.4577844        NA  
133001 1.7922814        NA  
133002 1.7884758 2.2312685  
133003 1.6063875        NA  
133004 1.8053753 3.7713942  
133005 1.6407190        NA  
133006 1.8335028        NA  
133007 2.8047358        NA  
133008 2.7363199        NA  
133009 2.4650343 2.4715503  
133010 2.7461729        NA  
133011 4.0746651        NA  
133012 1.7231710 1.6352917  
133013 2.1497159 2.0973007  
133014 2.6646192        NA  
133015 2.1512371        NA  
133016 5.1660144        NA  
133017 3.0822090        NA  
133018 3.8422268        NA  
133019 3.9732722        NA  
133020 3.5723555        NA  
133021 2.0669086 2.1297776  
133022 2.1999522        NA  
133023 2.1947101        NA  
⋮      ⋮         ⋮          
138440        NA        NA  
138441        NA        NA  
138442        NA        NA  
138443        NA        NA  
138444        NA        NA  
138445        NA        NA  
138446        NA        NA  
138447        NA        NA  
138448        NA        NA  
138450        NA        NA  
138451        NA        NA  
138452        NA        NA  
138453        NA        NA  
138455        NA        NA  
138456        NA        NA  
138457        NA        NA  
138458        NA        NA  
138459        NA        NA  
138460        NA        NA  
138461        NA        NA  
138497 0.5685982 0.4795761  
138498        NA        NA  
138499        NA        NA  
138500        NA        NA  
138501        NA        NA  
138502        NA        NA  
138503        NA        NA  
138504        NA        NA  
138505        NA        NA  
138506        NA        NA

In [175]:
trips_RMSE_r1_d0 = aggregate_trips('1', '0')
trips_RMSE_r1_d0

[1] "132994"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double(),
  ZIP_RMSE = col_double(),
  ZINB_RMSE = col_double(),
  Hurdle_RMSE = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "132995"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double(),
  ZIP_RMSE = col_double(),
  ZINB_RMSE = col_double(),
  Hurdle_RMSE = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "132996"


...

[1] "138427"
[1] "138428"
[1] "138429"
[1] "138430"
[1] "138431"
[1] "138432"
[1] "138433"
[1] "138434"
[1] "138435"
[1] "138436"
[1] "138437"
[1] "138438"
[1] "138439"
[1] "138440"
[1] "138441"
[1] "138442"
[1] "138443"
[1] "138444"
[1] "138445"
[1] "138446"
[1] "138447"
[1] "138448"
[1] "138450"
[1] "138451"
[1] "138452"
[1] "138453"
[1] "138455"
[1] "138456"
[1] "138457"
[1] "138458"
[1] "138459"
[1] "138460"
[1] "138461"
[1] "138497"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "138498"
[1] "138499"
[1] "138500"
[1] "138501"
[1] "138502"
[1] "138503"
[1] "138504"
[1] "138505"
[1] "138506"


Warning message in cbind(Poiss = test_RMSE_Poiss, NB = test_RMSE_NB, ZIP = test_RMSE_ZIP, :
“number of rows of result is not a multiple of vector length (arg 1)”


Poiss    NB       ZIP       ZINB     Hurdle    RF Zero_Inf_RF
132994 1.136528 1.136527 1.1536771 1.153333 1.1305326 NA NA         
132995 1.223552 1.223559 0.8104716 0.808239 0.7383299 NA NA         
132996       NA       NA        NA       NA        NA NA NA         
132997       NA       NA        NA       NA        NA NA NA         
132998       NA       NA        NA       NA        NA NA NA         
132999 3.142012 3.142084 3.2245968 3.224908 3.2185645 NA NA         
133000       NA       NA        NA       NA        NA NA NA         
133001 1.885068 1.885068 1.8850676 1.885066 1.8849131 NA NA         
133002 1.800966 1.800965 1.7937824 1.793630 1.7871431 NA NA         
133003       NA       NA        NA       NA        NA NA NA         
133004       NA       NA        NA       NA        NA NA NA         
133005 1.688233 1.688200 1.6894133 1.688944 1.6928134 NA NA         
133006       NA       NA        NA       NA        NA NA NA         
133007 2.810210 2.810549 2.8414469 2.841414 2.8417015 NA NA         
133008       NA       NA        NA       NA        NA NA NA         
133009 2.490501 2.457456 2.4878028 2.460928 2.4836283 NA NA         
133010       NA       NA        NA       NA        NA NA NA         
133011       NA       NA        NA       NA        NA NA NA         
133012 1.648944 1.652749 1.6496654 1.650685 1.6483162 NA NA         
133013 2.100476 2.098927 2.1006579 2.099846 2.1014651 NA NA         
133014       NA       NA        NA       NA        NA NA NA         
133015 2.176778 2.183549 2.1527319 2.157347 2.1498421 NA NA         
133016       NA       NA        NA       NA        NA NA NA         
133017       NA       NA        NA       NA        NA NA NA         
133018 3.748419 3.733110 3.6807786 3.664125 3.6863761 NA NA         
133019       NA       NA        NA       NA        NA NA NA         
133020       NA       NA        NA       NA        NA NA NA         
133021 2.143736 2.138318 2.1592058 2.158332 2.1648673 NA NA         
133022       NA       NA        NA       NA        NA NA NA         
133023       NA       NA        NA       NA        NA NA NA         
⋮      ⋮        ⋮        ⋮         ⋮        ⋮         ⋮  ⋮          
138440       NA       NA        NA       NA        NA NA NA         
138441       NA       NA        NA       NA        NA NA NA         
138442       NA       NA        NA       NA        NA NA NA         
138443       NA       NA        NA       NA        NA NA NA         
138444       NA       NA        NA       NA        NA NA NA         
138445       NA       NA        NA       NA        NA NA NA         
138446       NA       NA        NA       NA        NA NA NA         
138447       NA       NA        NA       NA        NA NA NA         
138448       NA       NA        NA       NA        NA NA NA         
138450       NA       NA        NA       NA        NA NA NA         
138451       NA       NA        NA       NA        NA NA NA         
138452       NA       NA        NA       NA        NA NA NA         
138453       NA       NA        NA       NA        NA NA NA         
138455       NA       NA        NA       NA        NA NA NA         
138456       NA       NA        NA       NA        NA NA NA         
138457       NA       NA        NA       NA        NA NA NA         
138458       NA       NA        NA       NA        NA NA NA         
138459       NA       NA        NA       NA        NA NA NA         
138460       NA       NA        NA       NA        NA NA NA         
138461       NA       NA        NA       NA        NA NA NA         
138497 1.136528 1.136527 1.1536771 1.153333 1.1305326 NA NA         
138498 1.223552 1.223559 0.8104716 0.808239 0.7383299 NA NA         
138499       NA       NA        NA       NA        NA NA NA         
138500       NA       NA        NA       NA        NA NA NA         
138501       NA       NA        NA       NA        NA NA NA         
138502 3.142012 3.142084 3.2245968 3.224908 3.2185645 NA NA         
13850

In [178]:
trips_RMSE_r1_d1 = aggregate_trips('1', '1')
trips_RMSE_r1_d1

[1] "133039"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double()
)




[1] "This trip did have enough data for meodeling"
[1] "133040"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double(),
  ZIP_RMSE = col_double(),
  ZINB_RMSE = col_double(),
  Hurdle_RMSE = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "133041"


...

[1] "138473"
[1] "138474"
[1] "138475"
[1] "138476"
[1] "138477"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "138478"
[1] "138480"
[1] "138481"
[1] "138482"
[1] "138483"
[1] "138484"
[1] "138486"
[1] "138487"
[1] "138488"
[1] "138489"
[1] "138491"
[1] "138492"
[1] "138493"
[1] "138494"
[1] "138495"
[1] "138496"
[1] "138507"
[1] "138508"
[1] "138509"
[1] "138510"
[1] "138511"
[1] "138512"
[1] "138513"
[1] "138514"
[1] "138515"
[1] "138516"


Warning message in cbind(Poiss = test_RMSE_Poiss, NB = test_RMSE_NB, ZIP = test_RMSE_ZIP, :
“number of rows of result is not a multiple of vector length (arg 1)”


Poiss    NB       ZIP      ZINB     Hurdle   RF Zero_Inf_RF
133039       NA       NA       NA       NA       NA NA NA         
133040 1.859883 1.859883 1.866914 1.866743 1.873670 NA NA         
133041 2.472557 2.472556 2.475002 2.474973 2.475752 NA NA         
133042 2.639305 2.649107 2.664059 2.668311 2.676340 NA NA         
133043       NA       NA       NA       NA       NA NA NA         
133044       NA       NA       NA       NA       NA NA NA         
133045       NA       NA       NA       NA       NA NA NA         
133046       NA       NA       NA       NA       NA NA NA         
133047 2.928530 2.929696 2.933654 2.932735 2.933725 NA NA         
133048       NA       NA       NA       NA       NA NA NA         
133049 3.400806 3.408802 3.408463 3.412856 3.410060 NA NA         
133050 3.419772 3.428684 3.446813 3.448013 3.450241 NA NA         
133051 2.950130 2.949808 2.949202 2.949386 2.948176 NA NA         
133052 2.826397 2.824638 2.833581 2.833084 2.834144 NA NA         
133053 2.397738 2.398166 2.401991 2.401595 2.403193 NA NA         
133054 2.494477 2.493975 2.497481 2.494193 2.501371 NA NA         
133055 4.076226 4.076429 4.063612 4.065754 4.062527 NA NA         
133056       NA       NA       NA       NA       NA NA NA         
133057 2.288010 2.286296 2.286980 2.286619 2.286459 NA NA         
133058 3.228113 3.234338 3.223375 3.227951 3.222807 NA NA         
133059 2.983535 2.984520 2.979681 2.980908 2.978551 NA NA         
133060       NA       NA       NA       NA       NA NA NA         
133061 3.864905 3.864893 4.077416 4.075214 4.078023 NA NA         
133062       NA       NA       NA       NA       NA NA NA         
133063       NA       NA       NA       NA       NA NA NA         
133064 2.694434 2.698343 2.705570 2.703632 2.710773 NA NA         
133065 3.396907 3.401831 3.361115 3.362645 3.356477 NA NA         
133066       NA       NA       NA       NA       NA NA NA         
133067 3.261030 3.265462 3.266769 3.268565 3.267762 NA NA         
133068 2.740483 2.740782 2.818797 2.802669 2.845920 NA NA         
⋮      ⋮        ⋮        ⋮        ⋮        ⋮        ⋮  ⋮          
138474       NA       NA       NA       NA       NA NA NA         
138475       NA       NA       NA       NA       NA NA NA         
138476       NA       NA       NA       NA       NA NA NA         
138477       NA       NA       NA       NA       NA NA NA         
138478       NA       NA       NA       NA       NA NA NA         
138480       NA       NA       NA       NA       NA NA NA         
138481       NA       NA       NA       NA       NA NA NA         
138482 1.859883 1.859883 1.866914 1.866743 1.873670 NA NA         
138483 2.472557 2.472556 2.475002 2.474973 2.475752 NA NA         
138484 2.639305 2.649107 2.664059 2.668311 2.676340 NA NA         
138486       NA       NA       NA       NA       NA NA NA         
138487       NA       NA       NA       NA       NA NA NA         
138488       NA       NA       NA       NA       NA NA NA         
138489       NA       NA       NA       NA       NA NA NA         
138491 2.928530 2.929696 2.933654 2.932735 2.933725 NA NA         
138492       NA       NA       NA       NA       NA NA NA         
138493 3.400806 3.408802 3.408463 3.412856 3.410060 NA NA         
138494 3.419772 3.428684 3.446813 3.448013 3.450241 NA NA         
138495 2.950130 2.949808 2.949202 2.949386 2.948176 NA NA         
138496 2.826397 2.824638 2.833581 2.833084 2.834144 NA NA         
138507 2.397738 2.398166 2.401991 2.401595 2.403193 NA NA         
138508 2.494477 2.493975 2.497481 2.494193 2.501371 NA NA         
138509 4.076226 4.076429 4.063612 4.065754 4.062527 NA NA         
138510       NA       NA       NA       NA       NA NA NA         
138511 2.288010 2.286296 2.286980 2.286619 2.286459 NA NA         
138512 3.228113 3.234338 3.223375 3.227951 3.222807 NA NA         
138513 2.983535 2.984520 2.979681 2.980908 2.978551 NA NA         
138514       NA       NA       NA       NA       NA NA

In [215]:
trips_RMSE_r1_d12 = aggregate_trips2('1', '1')
trips_RMSE_r1_d12

[1] "133039"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "133040"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "133041"


...

Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "138473"
[1] "138474"
[1] "138475"
[1] "138476"
[1] "138477"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "138478"
[1] "138480"
[1] "138481"
[1] "138482"
[1] "138483"
[1] "138484"
[1] "138486"
[1] "138487"
[1] "138488"
[1] "138489"
[1] "138491"
[1] "138492"
[1] "138493"
[1] "138494"
[1] "138495"
[1] "138496"
[1] "138507"
[1] "138508"
[1] "138509"
[1] "138510"
[1] "138511"
[1] "138512"
[1] "138513"
[1] "138514"
[1] "138515"
[1] "138516"


RF       Zero_Inf_RF
133039 3.414085       NA   
133040 1.918660       NA   
133041 3.049381       NA   
133042 2.427697       NA   
133043 2.693207       NA   
133044 3.555540       NA   
133045 3.538930       NA   
133046 4.657615       NA   
133047 4.159490       NA   
133048 2.588933       NA   
133049 2.976911       NA   
133050 2.843118       NA   
133051 3.353275       NA   
133052 3.777579 3.889893   
133053 2.922148       NA   
133054 2.998283 3.712218   
133055 2.720938       NA   
133056 2.464447       NA   
133057 4.020855       NA   
133058 3.353383       NA   
133059 2.294733       NA   
133060 3.170174       NA   
133061 3.053523 3.832290   
133062 3.054810       NA   
133063 3.599580 5.143531   
133064 3.092848       NA   
133065 3.190218       NA   
133066 2.736732       NA   
133067 3.305487 3.984991   
133068 3.397225       NA   
⋮      ⋮        ⋮          
138474       NA NA         
138475       NA NA         
138476       NA NA         
138477 2.657895 NA         
138478       NA NA         
138480       NA NA         
138481       NA NA         
138482       NA NA         
138483       NA NA         
138484       NA NA         
138486       NA NA         
138487       NA NA         
138488       NA NA         
138489       NA NA         
138491       NA NA         
138492       NA NA         
138493       NA NA         
138494       NA NA         
138495       NA NA         
138496       NA NA         
138507       NA NA         
138508       NA NA         
138509       NA NA         
138510       NA NA         
138511       NA NA         
138512       NA NA         
138513       NA NA         
138514       NA NA         
138515       NA NA         
138516       NA NA

In [180]:
trips_RMSE_r4_d0 = aggregate_trips('4', '0')
trips_RMSE_r4_d0

[1] "134296"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double(),
  ZIP_RMSE = col_double(),
  ZINB_RMSE = col_double(),
  Hurdle_RMSE = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "134297"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double(),
  ZIP_RMSE = col_double(),
  ZINB_RMSE = col_double(),
  Hurdle_RMSE = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "134298"


...

[1] "139760"
[1] "139761"
[1] "139762"
[1] "139763"
[1] "139764"
[1] "139765"
[1] "139766"
[1] "139767"
[1] "139768"
[1] "139769"
[1] "139770"
[1] "139771"
[1] "139772"
[1] "139773"
[1] "139774"
[1] "139775"
[1] "139776"
[1] "139777"
[1] "139778"
[1] "139779"
[1] "139780"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "139781"
[1] "139782"
[1] "139783"
[1] "139784"
[1] "139785"
[1] "139786"
[1] "139787"
[1] "139788"
[1] "139789"
[1] "139790"
[1] "139791"
[1] "139792"
[1] "139793"
[1] "139794"
[1] "139795"
[1] "139796"
[1] "139797"
[1] "139798"
[1] "139799"
[1] "139800"
[1] "139842"
[1] "139843"
[1] "139844"
[1] "139845"
[1] "139846"
[1] "139847"
[1] "139848"
[1] "139849"
[1] "139850"
[1] "139851"
[1] "139852"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message in cbind(Poiss = test_RMSE_Poiss, NB = test_RMSE_NB, ZIP = test_RMSE_ZIP, :
“number of rows of result is not a multiple of vector length (arg 1)”


Poiss    NB        ZIP      ZINB     Hurdle   RF Zero_Inf_RF
134296 2.083884  1.985831 1.883613 1.883460 1.912031 NA NA         
134297 6.576531 10.336459 6.362037 8.237559 6.613124 NA NA         
134298 3.981371  3.983141 3.976443 3.977796 3.974939 NA NA         
134299       NA        NA       NA       NA       NA NA NA         
134300       NA        NA       NA       NA       NA NA NA         
134301 3.620734  3.629164 3.701752 3.701969 3.701800 NA NA         
134302       NA        NA       NA       NA       NA NA NA         
134303 1.521203  1.521203 1.521151 1.521204 1.520382 NA NA         
134304 1.794539  1.788669 1.786920 1.773590 1.782373 NA NA         
134305 3.408898  3.403795 3.396042 3.392409 3.395539 NA NA         
134306 3.006528  3.006646 2.998202 2.998241 2.997187 NA NA         
134307 4.116203  4.092270 4.036497 3.226240 4.052845 NA NA         
134308 2.259374  2.262018 2.252121 2.254459 2.252620 NA NA         
134309       NA        NA       NA       NA       NA NA NA         
134310       NA        NA       NA       NA       NA NA NA         
134311       NA        NA       NA       NA       NA NA NA         
134312 4.884226  5.332518 4.395024 4.544522 4.394183 NA NA         
134313 2.199654  2.199655 2.416135 2.416130 2.416156 NA NA         
134314       NA        NA       NA       NA       NA NA NA         
134315       NA        NA       NA       NA       NA NA NA         
134316       NA        NA       NA       NA       NA NA NA         
134317 5.230209  5.233620 5.295833 5.299457 5.295912 NA NA         
134318 4.213896  4.402958 4.018409 4.139684 4.017863 NA NA         
134319       NA        NA       NA       NA       NA NA NA         
134320       NA        NA       NA       NA       NA NA NA         
134321       NA        NA       NA       NA       NA NA NA         
134322 4.867495  4.868422 4.855591 4.856823 4.855521 NA NA         
134323       NA        NA       NA       NA       NA NA NA         
134324 5.262672  5.273670 5.342408 5.342172 5.342391 NA NA         
134325 5.516099  5.671178 5.419734 5.466956 5.409893 NA NA         
⋮      ⋮        ⋮         ⋮        ⋮        ⋮        ⋮  ⋮          
139782       NA        NA       NA       NA       NA NA NA         
139783       NA        NA       NA       NA       NA NA NA         
139784       NA        NA       NA       NA       NA NA NA         
139785       NA        NA       NA       NA       NA NA NA         
139786       NA        NA       NA       NA       NA NA NA         
139787       NA        NA       NA       NA       NA NA NA         
139788       NA        NA       NA       NA       NA NA NA         
139789       NA        NA       NA       NA       NA NA NA         
139790       NA        NA       NA       NA       NA NA NA         
139791       NA        NA       NA       NA       NA NA NA         
139792       NA        NA       NA       NA       NA NA NA         
139793       NA        NA       NA       NA       NA NA NA         
139794       NA        NA       NA       NA       NA NA NA         
139795       NA        NA       NA       NA       NA NA NA         
139796       NA        NA       NA       NA       NA NA NA         
139797       NA        NA       NA       NA       NA NA NA         
139798       NA        NA       NA       NA       NA NA NA         
139799       NA        NA       NA       NA       NA NA NA         
139800       NA        NA       NA       NA       NA NA NA         
139842       NA        NA       NA       NA       NA NA NA         
139843       NA        NA       NA       NA       NA NA NA         
139844       NA        NA       NA       NA       NA NA NA         
139845       NA        NA       NA       NA       NA NA NA         
139846       NA        NA       NA       NA       NA NA NA         
139847       NA        NA       NA       NA       NA NA NA         
139848 2.083884  1.985831 1.883613 1.883460 1.912031 NA NA         
139849 6.576531 10.336459 6.362037 8.237559 6.613124 NA NA     

In [216]:
trips_RMSE_r4_d02 = aggregate_trips2('4', '0')
trips_RMSE_r4_d02

[1] "134296"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "134297"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "134298"


...

[1] "139760"
[1] "139761"
[1] "139762"
[1] "139763"
[1] "139764"
[1] "139765"
[1] "139766"
[1] "139767"
[1] "139768"
[1] "139769"
[1] "139770"
[1] "139771"
[1] "139772"
[1] "139773"
[1] "139774"
[1] "139775"
[1] "139776"
[1] "139777"
[1] "139778"
[1] "139779"
[1] "139780"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "139781"
[1] "139782"
[1] "139783"
[1] "139784"
[1] "139785"
[1] "139786"
[1] "139787"
[1] "139788"
[1] "139789"
[1] "139790"
[1] "139791"
[1] "139792"
[1] "139793"
[1] "139794"
[1] "139795"
[1] "139796"
[1] "139797"
[1] "139798"
[1] "139799"
[1] "139800"
[1] "139842"
[1] "139843"
[1] "139844"
[1] "139845"
[1] "139846"
[1] "139847"
[1] "139848"
[1] "139849"
[1] "139850"
[1] "139851"
[1] "139852"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




RF       Zero_Inf_RF
134296 1.824719 1.900179   
134297 2.729084 6.940793   
134298 3.909915       NA   
134299 4.762993       NA   
134300 5.644869       NA   
134301 3.577198       NA   
134302 5.332114       NA   
134303 1.504210 1.899321   
134304 1.737648 2.115850   
134305 3.632388       NA   
134306 3.121263       NA   
134307 2.950208 6.708086   
134308 2.889745       NA   
134309 3.812357       NA   
134310 4.004675       NA   
134311 4.062802       NA   
134312 2.900946 3.271389   
134313 2.030371       NA   
134314 1.768751       NA   
134315 4.112599       NA   
134316 4.621726       NA   
134317 5.290291       NA   
134318 2.639280       NA   
134319 4.319837       NA   
134320 4.992360       NA   
134321 4.709037       NA   
134322 4.875636       NA   
134323 4.706358       NA   
134324 5.282222       NA   
134325 3.663375 4.508325   
⋮      ⋮        ⋮          
139782       NA NA         
139783       NA NA         
139784       NA NA         
139785       NA NA         
139786       NA NA         
139787       NA NA         
139788       NA NA         
139789       NA NA         
139790       NA NA         
139791       NA NA         
139792       NA NA         
139793       NA NA         
139794       NA NA         
139795       NA NA         
139796       NA NA         
139797       NA NA         
139798       NA NA         
139799       NA NA         
139800       NA NA         
139842       NA NA         
139843       NA NA         
139844       NA NA         
139845       NA NA         
139846       NA NA         
139847       NA NA         
139848       NA NA         
139849       NA NA         
139850       NA NA         
139851       NA NA         
139852 5.918851 NA

In [182]:
trips_RMSE_r4_d1 = aggregate_trips('4', '1')
trips_RMSE_r4_d1

[1] "134364"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double()
)




[1] "This trip did have enough data for meodeling"
[1] "134365"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double()
)




[1] "This trip did have enough data for meodeling"
[1] "134366"


...

[1] "139833"
[1] "139834"
[1] "139835"
[1] "139836"
[1] "139837"
[1] "139838"
[1] "139839"
[1] "139840"
[1] "139841"
[1] "139853"
[1] "139854"
[1] "139855"
[1] "139856"
[1] "139857"
[1] "139858"
[1] "139859"
[1] "139860"
[1] "139861"
[1] "139862"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "139863"


Warning message in cbind(Poiss = test_RMSE_Poiss, NB = test_RMSE_NB, ZIP = test_RMSE_ZIP, :
“number of rows of result is not a multiple of vector length (arg 1)”


Poiss    NB       ZIP      ZINB     Hurdle   RF Zero_Inf_RF
134364       NA       NA       NA       NA       NA NA NA         
134365       NA       NA       NA       NA       NA NA NA         
134366       NA       NA       NA       NA       NA NA NA         
134367 2.632824 2.635899 2.631639 2.634436 2.631316 NA NA         
134368       NA       NA       NA       NA       NA NA NA         
134369 5.492949 5.522576 5.050526 4.799289 5.150213 NA NA         
134370       NA       NA       NA       NA       NA NA NA         
134371       NA       NA       NA       NA       NA NA NA         
134372       NA       NA       NA       NA       NA NA NA         
134373       NA       NA       NA       NA       NA NA NA         
134374       NA       NA       NA       NA       NA NA NA         
134375       NA       NA       NA       NA       NA NA NA         
134376       NA       NA       NA       NA       NA NA NA         
134377 3.073690 3.077794 3.048433 3.050974 3.047090 NA NA         
134378 4.420997 4.612129 4.067021 4.132455 4.066366 NA NA         
134379       NA       NA       NA       NA       NA NA NA         
134380 3.006178 3.006082 2.986414 2.986739 2.983867 NA NA         
134381 5.285675 5.293471 5.085620 4.753112 5.096942 NA NA         
134382 2.585227 2.584859 2.722061 2.722238 2.723735 NA NA         
134383       NA       NA       NA       NA       NA NA NA         
134384       NA       NA       NA       NA       NA NA NA         
134385       NA       NA       NA       NA       NA NA NA         
134386       NA       NA       NA       NA       NA NA NA         
134387 3.102643 3.112021 3.048350 3.050324 3.049349 NA NA         
134388 5.305211 5.359793 5.073298 4.862317 5.078835 NA NA         
134389 6.378701 6.355215 6.323098 6.300937 6.323114 NA NA         
134390       NA       NA       NA       NA       NA NA NA         
134391       NA       NA       NA       NA       NA NA NA         
134392       NA       NA       NA       NA       NA NA NA         
134393 5.465547 5.483706 5.382485 5.393514 5.382649 NA NA         
⋮      ⋮        ⋮        ⋮        ⋮        ⋮        ⋮  ⋮          
139823       NA       NA       NA       NA       NA NA NA         
139824       NA       NA       NA       NA       NA NA NA         
139825       NA       NA       NA       NA       NA NA NA         
139826       NA       NA       NA       NA       NA NA NA         
139827       NA       NA       NA       NA       NA NA NA         
139828       NA       NA       NA       NA       NA NA NA         
139829       NA       NA       NA       NA       NA NA NA         
139830       NA       NA       NA       NA       NA NA NA         
139831       NA       NA       NA       NA       NA NA NA         
139832       NA       NA       NA       NA       NA NA NA         
139833       NA       NA       NA       NA       NA NA NA         
139834       NA       NA       NA       NA       NA NA NA         
139835       NA       NA       NA       NA       NA NA NA         
139836       NA       NA       NA       NA       NA NA NA         
139837       NA       NA       NA       NA       NA NA NA         
139838       NA       NA       NA       NA       NA NA NA         
139839       NA       NA       NA       NA       NA NA NA         
139840       NA       NA       NA       NA       NA NA NA         
139841       NA       NA       NA       NA       NA NA NA         
139853       NA       NA       NA       NA       NA NA NA         
139854       NA       NA       NA       NA       NA NA NA         
139855       NA       NA       NA       NA       NA NA NA         
139856       NA       NA       NA       NA       NA NA NA         
139857       NA       NA       NA       NA       NA NA NA         
139858       NA       NA       NA       NA       NA NA NA         
139859 2.632824 2.635899 2.631639 2.634436 2.631316 NA NA         
139860       NA       NA       NA       NA       NA NA NA         
139861 5.492949 5.522576 5.050526 4.799289 5.150213 NA

In [217]:
trips_RMSE_r4_d12 = aggregate_trips2('4', '1')
trips_RMSE_r4_d12

[1] "134364"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "134365"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "134366"


...

Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "139833"
[1] "139834"
[1] "139835"
[1] "139836"
[1] "139837"
[1] "139838"
[1] "139839"
[1] "139840"
[1] "139841"
[1] "139853"
[1] "139854"
[1] "139855"
[1] "139856"
[1] "139857"
[1] "139858"
[1] "139859"
[1] "139860"
[1] "139861"
[1] "139862"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "139863"


RF       Zero_Inf_RF
134364 3.198935       NA   
134365 3.507241       NA   
134366 3.356626       NA   
134367 2.948924       NA   
134368 4.547593       NA   
134369 3.549669 4.419396   
134370 3.513704       NA   
134371 3.825233       NA   
134372 4.652667       NA   
134373 3.759153       NA   
134374 4.277551       NA   
134375 3.509133       NA   
134376 3.611453       NA   
134377 3.209222       NA   
134378 3.065135       NA   
134379 3.662887       NA   
134380 3.050583       NA   
134381 3.595930 4.571211   
134382 2.692833 4.764080   
134383 2.177022       NA   
134384 2.191779       NA   
134385 3.709607       NA   
134386 4.593798       NA   
134387 3.289336       NA   
134388 3.321187 3.741336   
134389 6.282659       NA   
134390 5.322329       NA   
134391 4.024718       NA   
134392 5.201769       NA   
134393 5.333223       NA   
⋮      ⋮        ⋮          
139823       NA      NA    
139824       NA      NA    
139825       NA      NA    
139826       NA      NA    
139827       NA      NA    
139828       NA      NA    
139829       NA      NA    
139830       NA      NA    
139831       NA      NA    
139832 1.765678 5.37816    
139833       NA      NA    
139834       NA      NA    
139835       NA      NA    
139836       NA      NA    
139837       NA      NA    
139838       NA      NA    
139839       NA      NA    
139840       NA      NA    
139841       NA      NA    
139853       NA      NA    
139854       NA      NA    
139855       NA      NA    
139856       NA      NA    
139857       NA      NA    
139858       NA      NA    
139859       NA      NA    
139860       NA      NA    
139861       NA      NA    
139862 3.251170      NA    
139863       NA      NA

In [184]:
trips_RMSE_r9_d0 = aggregate_trips('9', '0')
trips_RMSE_r9_d0

[1] "134767"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double(),
  ZIP_RMSE = col_double(),
  ZINB_RMSE = col_double(),
  Hurdle_RMSE = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "134768"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double(),
  ZIP_RMSE = col_double(),
  ZINB_RMSE = col_double(),
  Hurdle_RMSE = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "134769"


...

[1] "140125"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double(),
  ZIP_RMSE = col_double(),
  ZINB_RMSE = col_double(),
  Hurdle_RMSE = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "140155"
[1] "140156"
[1] "140157"
[1] "140158"
[1] "140159"
[1] "140160"
[1] "140161"
[1] "140162"
[1] "140163"
[1] "140164"
[1] "140165"
[1] "140166"
[1] "140167"
[1] "140168"
[1] "140169"
[1] "140170"
[1] "140171"
[1] "140172"
[1] "140173"
[1] "140174"
[1] "140197"
[1] "140198"
[1] "140199"
[1] "140200"
[1] "140201"
[1] "140202"
[1] "140203"
[1] "140204"
[1] "140205"


Warning message in cbind(Poiss = test_RMSE_Poiss, NB = test_RMSE_NB, ZIP = test_RMSE_ZIP, :
“number of rows of result is not a multiple of vector length (arg 1)”


Poiss    NB       ZIP      ZINB     Hurdle   RF Zero_Inf_RF
134767 1.455042 1.486337 1.492272 1.505847 1.495532 NA NA         
134768 2.557372 2.564529 2.544393 2.551573 2.543504 NA NA         
134769 2.342249 2.342250 2.394632 2.395064 2.401533 NA NA         
134770 2.533539 2.537487 2.533544 2.537487 2.543992 NA NA         
134771       NA       NA       NA       NA       NA NA NA         
134772 2.755871 2.755856 2.754332 2.754329 2.756598 NA NA         
134773       NA       NA       NA       NA       NA NA NA         
134774 1.445232 1.447900 1.481752 1.482791 1.479644 NA NA         
134775 2.322347 2.322960 2.330222 2.325634 2.321818 NA NA         
134776       NA       NA       NA       NA       NA NA NA         
134777 2.817300 2.816946 2.848940 2.847149 2.850848 NA NA         
134778 3.669198 3.668577 3.666881 3.665961 3.667846 NA NA         
134779 2.528460 2.529690 2.552365 2.553299 2.550906 NA NA         
134780       NA       NA       NA       NA       NA NA NA         
134781 3.772405 3.774553 3.776698 3.776673 3.777515 NA NA         
134782 4.012908 4.014546 4.015071 4.017664 4.018342 NA NA         
134783 2.167304 2.167307 2.168342 2.168336 2.168389 NA NA         
134784 2.690094 2.702015 2.700694 2.705396 2.700751 NA NA         
134785       NA       NA       NA       NA       NA NA NA         
134786       NA       NA       NA       NA       NA NA NA         
134787       NA       NA       NA       NA       NA NA NA         
134788 2.997489 2.998020 3.064148 3.056748 3.065946 NA NA         
134789 2.887912 2.889426 2.870308 2.870444 2.870478 NA NA         
134790       NA       NA       NA       NA       NA NA NA         
134791       NA       NA       NA       NA       NA NA NA         
134792       NA       NA       NA       NA       NA NA NA         
134793       NA       NA       NA       NA       NA NA NA         
134794       NA       NA       NA       NA       NA NA NA         
134795       NA       NA       NA       NA       NA NA NA         
134825       NA       NA       NA       NA       NA NA NA         
⋮      ⋮        ⋮        ⋮        ⋮        ⋮        ⋮  ⋮          
140125       NA       NA       NA       NA       NA NA NA         
140155       NA       NA       NA       NA       NA NA NA         
140156       NA       NA       NA       NA       NA NA NA         
140157       NA       NA       NA       NA       NA NA NA         
140158       NA       NA       NA       NA       NA NA NA         
140159       NA       NA       NA       NA       NA NA NA         
140160       NA       NA       NA       NA       NA NA NA         
140161       NA       NA       NA       NA       NA NA NA         
140162       NA       NA       NA       NA       NA NA NA         
140163       NA       NA       NA       NA       NA NA NA         
140164       NA       NA       NA       NA       NA NA NA         
140165       NA       NA       NA       NA       NA NA NA         
140166       NA       NA       NA       NA       NA NA NA         
140167       NA       NA       NA       NA       NA NA NA         
140168       NA       NA       NA       NA       NA NA NA         
140169       NA       NA       NA       NA       NA NA NA         
140170       NA       NA       NA       NA       NA NA NA         
140171       NA       NA       NA       NA       NA NA NA         
140172       NA       NA       NA       NA       NA NA NA         
140173       NA       NA       NA       NA       NA NA NA         
140174       NA       NA       NA       NA       NA NA NA         
140197       NA       NA       NA       NA       NA NA NA         
140198 1.455042 1.486337 1.492272 1.505847 1.495532 NA NA         
140199 2.557372 2.564529 2.544393 2.551573 2.543504 NA NA         
140200 2.342249 2.342250 2.394632 2.395064 2.401533 NA NA         
140201 2.533539 2.537487 2.533544 2.537487 2.543992 NA NA         
140202       NA       NA       NA       NA       NA NA NA         
140203 2.755871 2.755856 2.754332 2.754329 2.756598 NA

In [218]:
trips_RMSE_r9_d02 = aggregate_trips2('9', '0')
trips_RMSE_r9_d02

[1] "134767"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "134768"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "134769"


...

Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "140125"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "140155"
[1] "140156"
[1] "140157"
[1] "140158"
[1] "140159"
[1] "140160"
[1] "140161"
[1] "140162"
[1] "140163"
[1] "140164"
[1] "140165"
[1] "140166"
[1] "140167"
[1] "140168"
[1] "140169"
[1] "140170"
[1] "140171"
[1] "140172"
[1] "140173"
[1] "140174"
[1] "140197"
[1] "140198"
[1] "140199"
[1] "140200"
[1] "140201"
[1] "140202"
[1] "140203"
[1] "140204"
[1] "140205"


RF       Zero_Inf_RF
134767 1.533515 1.529583   
134768 2.424495 3.428426   
134769 2.267227       NA   
134770 2.511558       NA   
134771 2.879000       NA   
134772 2.722012       NA   
134773 2.777543       NA   
134774 1.443763 1.699262   
134775 2.390313       NA   
134776 2.598616       NA   
134777 2.799455       NA   
134778 3.634320 3.772507   
134779 2.554269 3.189885   
134780 3.387272       NA   
134781 3.865719 4.058244   
134782 4.062924       NA   
134783 2.167604       NA   
134784 2.725570 3.318977   
134785 2.766144       NA   
134786 4.458123       NA   
134787 2.882309       NA   
134788 3.066773       NA   
134789 2.931194 3.266884   
134790       NA       NA   
134791       NA       NA   
134792       NA       NA   
134793 2.808597       NA   
134794 3.645106       NA   
134795 4.340328       NA   
134825       NA       NA   
⋮      ⋮        ⋮          
140125 4.562125 NA         
140155       NA NA         
140156       NA NA         
140157       NA NA         
140158       NA NA         
140159       NA NA         
140160       NA NA         
140161       NA NA         
140162       NA NA         
140163       NA NA         
140164       NA NA         
140165       NA NA         
140166       NA NA         
140167       NA NA         
140168       NA NA         
140169       NA NA         
140170       NA NA         
140171       NA NA         
140172       NA NA         
140173       NA NA         
140174       NA NA         
140197       NA NA         
140198       NA NA         
140199       NA NA         
140200       NA NA         
140201       NA NA         
140202       NA NA         
140203       NA NA         
140204       NA NA         
140205       NA NA

In [185]:
trips_RMSE_r9_d1 = aggregate_trips('9', '1')
trips_RMSE_r9_d1

[1] "134796"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double()
)




[1] "This trip did have enough data for meodeling"
[1] "134797"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double()
)




[1] "This trip did have enough data for meodeling"
[1] "134798"


...

[1] "140154"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Poiss_RMSE = col_double(),
  NB_RMSE = col_double()
)




[1] "This trip did have enough data for meodeling"
[1] "140176"
[1] "140177"
[1] "140178"
[1] "140179"
[1] "140180"
[1] "140181"
[1] "140182"
[1] "140183"
[1] "140184"
[1] "140185"
[1] "140186"
[1] "140187"
[1] "140188"
[1] "140189"
[1] "140190"
[1] "140191"
[1] "140192"
[1] "140193"
[1] "140194"
[1] "140195"
[1] "140206"
[1] "140207"
[1] "140208"
[1] "140209"
[1] "140210"
[1] "140211"
[1] "140212"
[1] "140213"
[1] "140214"


Warning message in cbind(Poiss = test_RMSE_Poiss, NB = test_RMSE_NB, ZIP = test_RMSE_ZIP, :
“number of rows of result is not a multiple of vector length (arg 1)”


Poiss    NB       ZIP      ZINB     Hurdle   RF Zero_Inf_RF
134796       NA       NA       NA       NA       NA NA NA         
134797       NA       NA       NA       NA       NA NA NA         
134798       NA       NA       NA       NA       NA NA NA         
134799 4.254330 4.252759 5.885289 5.887883 5.885243 NA NA         
134800       NA       NA       NA       NA       NA NA NA         
134801       NA       NA       NA       NA       NA NA NA         
134802       NA       NA       NA       NA       NA NA NA         
134803       NA       NA       NA       NA       NA NA NA         
134804 3.254652 3.248230 3.259440 3.250706 3.261034 NA NA         
134805 2.881842 2.882598 2.873967 2.873943 2.873882 NA NA         
134806       NA       NA       NA       NA       NA NA NA         
134807       NA       NA       NA       NA       NA NA NA         
134808       NA       NA       NA       NA       NA NA NA         
134809 4.545670 4.543819 4.545478 4.544519 4.545607 NA NA         
134810 1.996242 1.999052 2.085196 2.128592 2.065481 NA NA         
134811 3.715253 3.699893 3.649071 3.653134 3.646827 NA NA         
134812       NA       NA       NA       NA       NA NA NA         
134813       NA       NA       NA       NA       NA NA NA         
134814 3.391729 3.391806 3.391785 3.391909 3.391854 NA NA         
134815 1.964722 1.964721 2.283869 2.283858 2.283939 NA NA         
134816 2.073805 2.076818 2.074928 2.072412 2.079790 NA NA         
134817 3.421087 3.421820 3.438129 3.438260 3.438024 NA NA         
134818 2.378060 2.375988 2.377232 2.374511 2.372102 NA NA         
134819       NA       NA       NA       NA       NA NA NA         
134820       NA       NA       NA       NA       NA NA NA         
134821       NA       NA       NA       NA       NA NA NA         
134822       NA       NA       NA       NA       NA NA NA         
134823 3.690704 3.697632 3.689425 3.685535 3.685555 NA NA         
134824       NA       NA       NA       NA       NA NA NA         
134846       NA       NA       NA       NA       NA NA NA         
⋮      ⋮        ⋮        ⋮        ⋮        ⋮        ⋮  ⋮          
140154       NA       NA       NA       NA       NA NA NA         
140176       NA       NA       NA       NA       NA NA NA         
140177       NA       NA       NA       NA       NA NA NA         
140178       NA       NA       NA       NA       NA NA NA         
140179       NA       NA       NA       NA       NA NA NA         
140180       NA       NA       NA       NA       NA NA NA         
140181       NA       NA       NA       NA       NA NA NA         
140182       NA       NA       NA       NA       NA NA NA         
140183       NA       NA       NA       NA       NA NA NA         
140184       NA       NA       NA       NA       NA NA NA         
140185       NA       NA       NA       NA       NA NA NA         
140186       NA       NA       NA       NA       NA NA NA         
140187       NA       NA       NA       NA       NA NA NA         
140188       NA       NA       NA       NA       NA NA NA         
140189       NA       NA       NA       NA       NA NA NA         
140190       NA       NA       NA       NA       NA NA NA         
140191       NA       NA       NA       NA       NA NA NA         
140192       NA       NA       NA       NA       NA NA NA         
140193       NA       NA       NA       NA       NA NA NA         
140194 4.254330 4.252759 5.885289 5.887883 5.885243 NA NA         
140195       NA       NA       NA       NA       NA NA NA         
140206       NA       NA       NA       NA       NA NA NA         
140207       NA       NA       NA       NA       NA NA NA         
140208       NA       NA       NA       NA       NA NA NA         
140209 3.254652 3.248230 3.259440 3.250706 3.261034 NA NA         
140210 2.881842 2.882598 2.873967 2.873943 2.873882 NA NA         
140211       NA       NA       NA       NA       NA NA NA         
140212       NA       NA       NA       NA       NA NA

In [219]:
trips_RMSE_r9_d12 = aggregate_trips2('9', '1')
trips_RMSE_r9_d12

[1] "134796"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "134797"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "134798"


...

Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_double(),
  hour = col_double(),
  max_occupancy = col_double(),
  mean_temp = col_double(),
  mean_precip = col_double(),
  RF_Pred = col_double()
)




[1] "140154"


Warning message:
“Missing column names filled in: 'X1' [1]”

── Column specification ────────────────────────────────────────────────────────
cols(
  X1 = col_character(),
  Train = col_double(),
  Test = col_double()
)




[1] "140176"
[1] "140177"
[1] "140178"
[1] "140179"
[1] "140180"
[1] "140181"
[1] "140182"
[1] "140183"
[1] "140184"
[1] "140185"
[1] "140186"
[1] "140187"
[1] "140188"
[1] "140189"
[1] "140190"
[1] "140191"
[1] "140192"
[1] "140193"
[1] "140194"
[1] "140195"
[1] "140206"
[1] "140207"
[1] "140208"
[1] "140209"
[1] "140210"
[1] "140211"
[1] "140212"
[1] "140213"
[1] "140214"


RF       Zero_Inf_RF
134796 5.838655       NA   
134797 4.650491       NA   
134798 3.088054       NA   
134799 4.180007       NA   
134800 3.461791       NA   
134801 4.332212       NA   
134802 4.511777       NA   
134803 2.780933       NA   
134804 3.393149       NA   
134805 3.126664       NA   
134806 3.435292       NA   
134807 3.244720       NA   
134808 3.128364       NA   
134809 5.610862       NA   
134810 1.965074 3.077790   
134811 2.696340       NA   
134812 2.891598       NA   
134813 3.091673       NA   
134814 3.406841       NA   
134815 2.050888       NA   
134816 2.068542 3.354309   
134817 3.571420       NA   
134818 2.483129 3.667265   
134819 3.623241       NA   
134820       NA       NA   
134821       NA       NA   
134822       NA       NA   
134823 3.751332       NA   
134824 2.197169       NA   
134846       NA       NA   
⋮      ⋮        ⋮          
140154 3.338596 NA         
140176       NA NA         
140177       NA NA         
140178       NA NA         
140179       NA NA         
140180       NA NA         
140181       NA NA         
140182       NA NA         
140183       NA NA         
140184       NA NA         
140185       NA NA         
140186       NA NA         
140187       NA NA         
140188       NA NA         
140189       NA NA         
140190       NA NA         
140191       NA NA         
140192       NA NA         
140193       NA NA         
140194       NA NA         
140195       NA NA         
140206       NA NA         
140207       NA NA         
140208       NA NA         
140209       NA NA         
140210       NA NA         
140211       NA NA         
140212       NA NA         
140213       NA NA         
140214       NA NA

In [ ]:
# RMSEs combined

## Route 1

### Direction 0

In [221]:
trips_RMSE_r1_d0$RF = trips_RMSE_r1_d02$RF
trips_RMSE_r1_d0$Zero_Inf_RF = trips_RMSE_r1_d02$Zero_Inf_RF
trips_RMSE_r1_d0

Poiss    NB       ZIP       ZINB     Hurdle    RF        Zero_Inf_RF
132994 1.136528 1.136527 1.1536771 1.153333 1.1305326 1.1736624 1.1154603  
132995 1.223552 1.223559 0.8104716 0.808239 0.7383299 0.7422244 0.5210501  
132996       NA       NA        NA       NA        NA 2.5287334        NA  
132997       NA       NA        NA       NA        NA 3.2488900        NA  
132998       NA       NA        NA       NA        NA 1.4017994 1.3268382  
132999 3.142012 3.142084 3.2245968 3.224908 3.2185645 3.0204008        NA  
133000       NA       NA        NA       NA        NA 1.4577844        NA  
133001 1.885068 1.885068 1.8850676 1.885066 1.8849131 1.7922814        NA  
133002 1.800966 1.800965 1.7937824 1.793630 1.7871431 1.7884758 2.2312685  
133003       NA       NA        NA       NA        NA 1.6063875        NA  
133004       NA       NA        NA       NA        NA 1.8053753 3.7713942  
133005 1.688233 1.688200 1.6894133 1.688944 1.6928134 1.6407190        NA  
133006       NA       NA        NA       NA        NA 1.8335028        NA  
133007 2.810210 2.810549 2.8414469 2.841414 2.8417015 2.8047358        NA  
133008       NA       NA        NA       NA        NA 2.7363199        NA  
133009 2.490501 2.457456 2.4878028 2.460928 2.4836283 2.4650343 2.4715503  
133010       NA       NA        NA       NA        NA 2.7461729        NA  
133011       NA       NA        NA       NA        NA 4.0746651        NA  
133012 1.648944 1.652749 1.6496654 1.650685 1.6483162 1.7231710 1.6352917  
133013 2.100476 2.098927 2.1006579 2.099846 2.1014651 2.1497159 2.0973007  
133014       NA       NA        NA       NA        NA 2.6646192        NA  
133015 2.176778 2.183549 2.1527319 2.157347 2.1498421 2.1512371        NA  
133016       NA       NA        NA       NA        NA 5.1660144        NA  
133017       NA       NA        NA       NA        NA 3.0822090        NA  
133018 3.748419 3.733110 3.6807786 3.664125 3.6863761 3.8422268        NA  
133019       NA       NA        NA       NA        NA 3.9732722        NA  
133020       NA       NA        NA       NA        NA 3.5723555        NA  
133021 2.143736 2.138318 2.1592058 2.158332 2.1648673 2.0669086 2.1297776  
133022       NA       NA        NA       NA        NA 2.1999522        NA  
133023       NA       NA        NA       NA        NA 2.1947101        NA  
⋮      ⋮        ⋮        ⋮         ⋮        ⋮         ⋮         ⋮          
138440       NA       NA        NA       NA        NA        NA        NA  
138441       NA       NA        NA       NA        NA        NA        NA  
138442       NA       NA        NA       NA        NA        NA        NA  
138443       NA       NA        NA       NA        NA        NA        NA  
138444       NA       NA        NA       NA        NA        NA        NA  
138445       NA       NA        NA       NA        NA        NA        NA  
138446       NA       NA        NA       NA        NA        NA        NA  
138447       NA       NA        NA       NA        NA        NA        NA  
138448       NA       NA        NA       NA        NA        NA        NA  
138450       NA       NA        NA       NA        NA        NA        NA  
138451       NA       NA        NA       NA        NA        NA        NA  
138452       NA       NA        NA       NA        NA        NA        NA  
138453       NA       NA        NA       NA        NA        NA        NA  
138455       NA       NA        NA       NA        NA        NA        NA  
138456       NA       NA        NA       NA        NA        NA        NA  
138457       NA       NA        NA       NA        NA        NA        NA  
138458       NA       NA        NA       NA        NA        NA        NA  
138459       NA       NA        NA       NA        NA        NA        NA  
138460       NA       NA        NA       NA        NA        NA        NA  
138461       NA       NA        NA       NA        NA        NA        NA  
138497 1.136528 1.136527 1.1536771 1.153333 1.1305326 0

In [224]:
write.csv(trips_RMSE_r1_d0, 'trips_RMSE_r1_d0.csv', row.names = F)

In [ ]:
### Direction 1

In [222]:
trips_RMSE_r1_d1$RF = trips_RMSE_r1_d12$RF
trips_RMSE_r1_d1$Zero_Inf_RF = trips_RMSE_r1_d12$Zero_Inf_RF
trips_RMSE_r1_d1

Poiss    NB       ZIP      ZINB     Hurdle   RF       Zero_Inf_RF
133039       NA       NA       NA       NA       NA 3.414085       NA   
133040 1.859883 1.859883 1.866914 1.866743 1.873670 1.918660       NA   
133041 2.472557 2.472556 2.475002 2.474973 2.475752 3.049381       NA   
133042 2.639305 2.649107 2.664059 2.668311 2.676340 2.427697       NA   
133043       NA       NA       NA       NA       NA 2.693207       NA   
133044       NA       NA       NA       NA       NA 3.555540       NA   
133045       NA       NA       NA       NA       NA 3.538930       NA   
133046       NA       NA       NA       NA       NA 4.657615       NA   
133047 2.928530 2.929696 2.933654 2.932735 2.933725 4.159490       NA   
133048       NA       NA       NA       NA       NA 2.588933       NA   
133049 3.400806 3.408802 3.408463 3.412856 3.410060 2.976911       NA   
133050 3.419772 3.428684 3.446813 3.448013 3.450241 2.843118       NA   
133051 2.950130 2.949808 2.949202 2.949386 2.948176 3.353275       NA   
133052 2.826397 2.824638 2.833581 2.833084 2.834144 3.777579 3.889893   
133053 2.397738 2.398166 2.401991 2.401595 2.403193 2.922148       NA   
133054 2.494477 2.493975 2.497481 2.494193 2.501371 2.998283 3.712218   
133055 4.076226 4.076429 4.063612 4.065754 4.062527 2.720938       NA   
133056       NA       NA       NA       NA       NA 2.464447       NA   
133057 2.288010 2.286296 2.286980 2.286619 2.286459 4.020855       NA   
133058 3.228113 3.234338 3.223375 3.227951 3.222807 3.353383       NA   
133059 2.983535 2.984520 2.979681 2.980908 2.978551 2.294733       NA   
133060       NA       NA       NA       NA       NA 3.170174       NA   
133061 3.864905 3.864893 4.077416 4.075214 4.078023 3.053523 3.832290   
133062       NA       NA       NA       NA       NA 3.054810       NA   
133063       NA       NA       NA       NA       NA 3.599580 5.143531   
133064 2.694434 2.698343 2.705570 2.703632 2.710773 3.092848       NA   
133065 3.396907 3.401831 3.361115 3.362645 3.356477 3.190218       NA   
133066       NA       NA       NA       NA       NA 2.736732       NA   
133067 3.261030 3.265462 3.266769 3.268565 3.267762 3.305487 3.984991   
133068 2.740483 2.740782 2.818797 2.802669 2.845920 3.397225       NA   
⋮      ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮          
138474       NA       NA       NA       NA       NA       NA NA         
138475       NA       NA       NA       NA       NA       NA NA         
138476       NA       NA       NA       NA       NA       NA NA         
138477       NA       NA       NA       NA       NA 2.657895 NA         
138478       NA       NA       NA       NA       NA       NA NA         
138480       NA       NA       NA       NA       NA       NA NA         
138481       NA       NA       NA       NA       NA       NA NA         
138482 1.859883 1.859883 1.866914 1.866743 1.873670       NA NA         
138483 2.472557 2.472556 2.475002 2.474973 2.475752       NA NA         
138484 2.639305 2.649107 2.664059 2.668311 2.676340       NA NA         
138486       NA       NA       NA       NA       NA       NA NA         
138487       NA       NA       NA       NA       NA       NA NA         
138488       NA       NA       NA       NA       NA       NA NA         
138489       NA       NA       NA       NA       NA       NA NA         
138491 2.928530 2.929696 2.933654 2.932735 2.933725       NA NA         
138492       NA       NA       NA       NA       NA       NA NA         
138493 3.400806 3.408802 3.408463 3.412856 3.410060       NA NA         
138494 3.419772 3.428684 3.446813 3.448013 3.450241       NA NA         
138495 2.950130 2.949808 2.949202 2.949386 2.948176       NA NA         
138496 2.826397 2.824638 2.833581 2.833084 2.834144       NA NA         
138507 2.397738 2.398166 2.401991 2.401595 2.403193       NA NA         
138508 2.494477 2.493975 2.497481 2.494193 2.501371       NA NA         
138509 4.076226 4.076429 4.063612 4.065754 4.062527       NA NA  

In [225]:
write.csv(trips_RMSE_r1_d1, 'trips_RMSE_r1_d1.csv', row.names = F)

In [ ]:
## Route 4

### Direction 0

In [226]:
trips_RMSE_r4_d0$RF = trips_RMSE_r4_d02$RF
trips_RMSE_r4_d0$Zero_Inf_RF = trips_RMSE_r4_d02$Zero_Inf_RF
trips_RMSE_r4_d0

Poiss    NB        ZIP      ZINB     Hurdle   RF       Zero_Inf_RF
134296 2.083884  1.985831 1.883613 1.883460 1.912031 1.824719 1.900179   
134297 6.576531 10.336459 6.362037 8.237559 6.613124 2.729084 6.940793   
134298 3.981371  3.983141 3.976443 3.977796 3.974939 3.909915       NA   
134299       NA        NA       NA       NA       NA 4.762993       NA   
134300       NA        NA       NA       NA       NA 5.644869       NA   
134301 3.620734  3.629164 3.701752 3.701969 3.701800 3.577198       NA   
134302       NA        NA       NA       NA       NA 5.332114       NA   
134303 1.521203  1.521203 1.521151 1.521204 1.520382 1.504210 1.899321   
134304 1.794539  1.788669 1.786920 1.773590 1.782373 1.737648 2.115850   
134305 3.408898  3.403795 3.396042 3.392409 3.395539 3.632388       NA   
134306 3.006528  3.006646 2.998202 2.998241 2.997187 3.121263       NA   
134307 4.116203  4.092270 4.036497 3.226240 4.052845 2.950208 6.708086   
134308 2.259374  2.262018 2.252121 2.254459 2.252620 2.889745       NA   
134309       NA        NA       NA       NA       NA 3.812357       NA   
134310       NA        NA       NA       NA       NA 4.004675       NA   
134311       NA        NA       NA       NA       NA 4.062802       NA   
134312 4.884226  5.332518 4.395024 4.544522 4.394183 2.900946 3.271389   
134313 2.199654  2.199655 2.416135 2.416130 2.416156 2.030371       NA   
134314       NA        NA       NA       NA       NA 1.768751       NA   
134315       NA        NA       NA       NA       NA 4.112599       NA   
134316       NA        NA       NA       NA       NA 4.621726       NA   
134317 5.230209  5.233620 5.295833 5.299457 5.295912 5.290291       NA   
134318 4.213896  4.402958 4.018409 4.139684 4.017863 2.639280       NA   
134319       NA        NA       NA       NA       NA 4.319837       NA   
134320       NA        NA       NA       NA       NA 4.992360       NA   
134321       NA        NA       NA       NA       NA 4.709037       NA   
134322 4.867495  4.868422 4.855591 4.856823 4.855521 4.875636       NA   
134323       NA        NA       NA       NA       NA 4.706358       NA   
134324 5.262672  5.273670 5.342408 5.342172 5.342391 5.282222       NA   
134325 5.516099  5.671178 5.419734 5.466956 5.409893 3.663375 4.508325   
⋮      ⋮        ⋮         ⋮        ⋮        ⋮        ⋮        ⋮          
139782       NA        NA       NA       NA       NA       NA NA         
139783       NA        NA       NA       NA       NA       NA NA         
139784       NA        NA       NA       NA       NA       NA NA         
139785       NA        NA       NA       NA       NA       NA NA         
139786       NA        NA       NA       NA       NA       NA NA         
139787       NA        NA       NA       NA       NA       NA NA         
139788       NA        NA       NA       NA       NA       NA NA         
139789       NA        NA       NA       NA       NA       NA NA         
139790       NA        NA       NA       NA       NA       NA NA         
139791       NA        NA       NA       NA       NA       NA NA         
139792       NA        NA       NA       NA       NA       NA NA         
139793       NA        NA       NA       NA       NA       NA NA         
139794       NA        NA       NA       NA       NA       NA NA         
139795       NA        NA       NA       NA       NA       NA NA         
139796       NA        NA       NA       NA       NA       NA NA         
139797       NA        NA       NA       NA       NA       NA NA         
139798       NA        NA       NA       NA       NA       NA NA         
139799       NA        NA       NA       NA       NA       NA NA         
139800       NA        NA       NA       NA       NA       NA NA         
139842       NA        NA       NA       NA       NA       NA NA         
139843       NA        NA       NA       NA       NA       NA NA         
139844       NA        NA       NA       NA       NA       NA NA         
139845     

In [227]:
write.csv(trips_RMSE_r4_d0, 'trips_RMSE_r4_d0.csv', row.names = F)

In [228]:
### Direction 1

In [229]:
trips_RMSE_r4_d1$RF = trips_RMSE_r4_d12$RF
trips_RMSE_r4_d1$Zero_Inf_RF = trips_RMSE_r4_d12$Zero_Inf_RF
trips_RMSE_r4_d1

Poiss    NB       ZIP      ZINB     Hurdle   RF       Zero_Inf_RF
134364       NA       NA       NA       NA       NA 3.198935       NA   
134365       NA       NA       NA       NA       NA 3.507241       NA   
134366       NA       NA       NA       NA       NA 3.356626       NA   
134367 2.632824 2.635899 2.631639 2.634436 2.631316 2.948924       NA   
134368       NA       NA       NA       NA       NA 4.547593       NA   
134369 5.492949 5.522576 5.050526 4.799289 5.150213 3.549669 4.419396   
134370       NA       NA       NA       NA       NA 3.513704       NA   
134371       NA       NA       NA       NA       NA 3.825233       NA   
134372       NA       NA       NA       NA       NA 4.652667       NA   
134373       NA       NA       NA       NA       NA 3.759153       NA   
134374       NA       NA       NA       NA       NA 4.277551       NA   
134375       NA       NA       NA       NA       NA 3.509133       NA   
134376       NA       NA       NA       NA       NA 3.611453       NA   
134377 3.073690 3.077794 3.048433 3.050974 3.047090 3.209222       NA   
134378 4.420997 4.612129 4.067021 4.132455 4.066366 3.065135       NA   
134379       NA       NA       NA       NA       NA 3.662887       NA   
134380 3.006178 3.006082 2.986414 2.986739 2.983867 3.050583       NA   
134381 5.285675 5.293471 5.085620 4.753112 5.096942 3.595930 4.571211   
134382 2.585227 2.584859 2.722061 2.722238 2.723735 2.692833 4.764080   
134383       NA       NA       NA       NA       NA 2.177022       NA   
134384       NA       NA       NA       NA       NA 2.191779       NA   
134385       NA       NA       NA       NA       NA 3.709607       NA   
134386       NA       NA       NA       NA       NA 4.593798       NA   
134387 3.102643 3.112021 3.048350 3.050324 3.049349 3.289336       NA   
134388 5.305211 5.359793 5.073298 4.862317 5.078835 3.321187 3.741336   
134389 6.378701 6.355215 6.323098 6.300937 6.323114 6.282659       NA   
134390       NA       NA       NA       NA       NA 5.322329       NA   
134391       NA       NA       NA       NA       NA 4.024718       NA   
134392       NA       NA       NA       NA       NA 5.201769       NA   
134393 5.465547 5.483706 5.382485 5.393514 5.382649 5.333223       NA   
⋮      ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮          
139823       NA       NA       NA       NA       NA       NA      NA    
139824       NA       NA       NA       NA       NA       NA      NA    
139825       NA       NA       NA       NA       NA       NA      NA    
139826       NA       NA       NA       NA       NA       NA      NA    
139827       NA       NA       NA       NA       NA       NA      NA    
139828       NA       NA       NA       NA       NA       NA      NA    
139829       NA       NA       NA       NA       NA       NA      NA    
139830       NA       NA       NA       NA       NA       NA      NA    
139831       NA       NA       NA       NA       NA       NA      NA    
139832       NA       NA       NA       NA       NA 1.765678 5.37816    
139833       NA       NA       NA       NA       NA       NA      NA    
139834       NA       NA       NA       NA       NA       NA      NA    
139835       NA       NA       NA       NA       NA       NA      NA    
139836       NA       NA       NA       NA       NA       NA      NA    
139837       NA       NA       NA       NA       NA       NA      NA    
139838       NA       NA       NA       NA       NA       NA      NA    
139839       NA       NA       NA       NA       NA       NA      NA    
139840       NA       NA       NA       NA       NA       NA      NA    
139841       NA       NA       NA       NA       NA       NA      NA    
139853       NA       NA       NA       NA       NA       NA      NA    
139854       NA       NA       NA       NA       NA       NA      NA    
139855       NA       NA       NA       NA       NA       NA      NA    
139856       NA       NA       NA       NA       NA       NA     

In [230]:
write.csv(trips_RMSE_r4_d1, 'trips_RMSE_r4_d1.csv', row.names = F)

In [ ]:
## Route 9

### Direction 0

In [236]:
trips_RMSE_r9_d0$RF = trips_RMSE_r9_d02$RF
trips_RMSE_r9_d0$Zero_Inf_RF = trips_RMSE_r9_d02$Zero_Inf_RF
trips_RMSE_r9_d0

Poiss    NB       ZIP      ZINB     Hurdle   RF       Zero_Inf_RF
134767 1.455042 1.486337 1.492272 1.505847 1.495532 1.533515 1.529583   
134768 2.557372 2.564529 2.544393 2.551573 2.543504 2.424495 3.428426   
134769 2.342249 2.342250 2.394632 2.395064 2.401533 2.267227       NA   
134770 2.533539 2.537487 2.533544 2.537487 2.543992 2.511558       NA   
134771       NA       NA       NA       NA       NA 2.879000       NA   
134772 2.755871 2.755856 2.754332 2.754329 2.756598 2.722012       NA   
134773       NA       NA       NA       NA       NA 2.777543       NA   
134774 1.445232 1.447900 1.481752 1.482791 1.479644 1.443763 1.699262   
134775 2.322347 2.322960 2.330222 2.325634 2.321818 2.390313       NA   
134776       NA       NA       NA       NA       NA 2.598616       NA   
134777 2.817300 2.816946 2.848940 2.847149 2.850848 2.799455       NA   
134778 3.669198 3.668577 3.666881 3.665961 3.667846 3.634320 3.772507   
134779 2.528460 2.529690 2.552365 2.553299 2.550906 2.554269 3.189885   
134780       NA       NA       NA       NA       NA 3.387272       NA   
134781 3.772405 3.774553 3.776698 3.776673 3.777515 3.865719 4.058244   
134782 4.012908 4.014546 4.015071 4.017664 4.018342 4.062924       NA   
134783 2.167304 2.167307 2.168342 2.168336 2.168389 2.167604       NA   
134784 2.690094 2.702015 2.700694 2.705396 2.700751 2.725570 3.318977   
134785       NA       NA       NA       NA       NA 2.766144       NA   
134786       NA       NA       NA       NA       NA 4.458123       NA   
134787       NA       NA       NA       NA       NA 2.882309       NA   
134788 2.997489 2.998020 3.064148 3.056748 3.065946 3.066773       NA   
134789 2.887912 2.889426 2.870308 2.870444 2.870478 2.931194 3.266884   
134790       NA       NA       NA       NA       NA       NA       NA   
134791       NA       NA       NA       NA       NA       NA       NA   
134792       NA       NA       NA       NA       NA       NA       NA   
134793       NA       NA       NA       NA       NA 2.808597       NA   
134794       NA       NA       NA       NA       NA 3.645106       NA   
134795       NA       NA       NA       NA       NA 4.340328       NA   
134825       NA       NA       NA       NA       NA       NA       NA   
⋮      ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮          
140125       NA       NA       NA       NA       NA 4.562125 NA         
140155       NA       NA       NA       NA       NA       NA NA         
140156       NA       NA       NA       NA       NA       NA NA         
140157       NA       NA       NA       NA       NA       NA NA         
140158       NA       NA       NA       NA       NA       NA NA         
140159       NA       NA       NA       NA       NA       NA NA         
140160       NA       NA       NA       NA       NA       NA NA         
140161       NA       NA       NA       NA       NA       NA NA         
140162       NA       NA       NA       NA       NA       NA NA         
140163       NA       NA       NA       NA       NA       NA NA         
140164       NA       NA       NA       NA       NA       NA NA         
140165       NA       NA       NA       NA       NA       NA NA         
140166       NA       NA       NA       NA       NA       NA NA         
140167       NA       NA       NA       NA       NA       NA NA         
140168       NA       NA       NA       NA       NA       NA NA         
140169       NA       NA       NA       NA       NA       NA NA         
140170       NA       NA       NA       NA       NA       NA NA         
140171       NA       NA       NA       NA       NA       NA NA         
140172       NA       NA       NA       NA       NA       NA NA         
140173       NA       NA       NA       NA       NA       NA NA         
140174       NA       NA       NA       NA       NA       NA NA         
140197       NA       NA       NA       NA       NA       NA NA         
140198 1.455042 1.486337 1.492272 1.505847 1.495532       NA NA  

In [237]:
write.csv(trips_RMSE_r9_d0, 'trips_RMSE_r9_d0.csv', row.names = F)

In [ ]:
### Direction 1

In [238]:
trips_RMSE_r9_d1$RF = trips_RMSE_r9_d12$RF
trips_RMSE_r9_d1$Zero_Inf_RF = trips_RMSE_r9_d12$Zero_Inf_RF
trips_RMSE_r9_d1

Poiss    NB       ZIP      ZINB     Hurdle   RF       Zero_Inf_RF
134796       NA       NA       NA       NA       NA 5.838655       NA   
134797       NA       NA       NA       NA       NA 4.650491       NA   
134798       NA       NA       NA       NA       NA 3.088054       NA   
134799 4.254330 4.252759 5.885289 5.887883 5.885243 4.180007       NA   
134800       NA       NA       NA       NA       NA 3.461791       NA   
134801       NA       NA       NA       NA       NA 4.332212       NA   
134802       NA       NA       NA       NA       NA 4.511777       NA   
134803       NA       NA       NA       NA       NA 2.780933       NA   
134804 3.254652 3.248230 3.259440 3.250706 3.261034 3.393149       NA   
134805 2.881842 2.882598 2.873967 2.873943 2.873882 3.126664       NA   
134806       NA       NA       NA       NA       NA 3.435292       NA   
134807       NA       NA       NA       NA       NA 3.244720       NA   
134808       NA       NA       NA       NA       NA 3.128364       NA   
134809 4.545670 4.543819 4.545478 4.544519 4.545607 5.610862       NA   
134810 1.996242 1.999052 2.085196 2.128592 2.065481 1.965074 3.077790   
134811 3.715253 3.699893 3.649071 3.653134 3.646827 2.696340       NA   
134812       NA       NA       NA       NA       NA 2.891598       NA   
134813       NA       NA       NA       NA       NA 3.091673       NA   
134814 3.391729 3.391806 3.391785 3.391909 3.391854 3.406841       NA   
134815 1.964722 1.964721 2.283869 2.283858 2.283939 2.050888       NA   
134816 2.073805 2.076818 2.074928 2.072412 2.079790 2.068542 3.354309   
134817 3.421087 3.421820 3.438129 3.438260 3.438024 3.571420       NA   
134818 2.378060 2.375988 2.377232 2.374511 2.372102 2.483129 3.667265   
134819       NA       NA       NA       NA       NA 3.623241       NA   
134820       NA       NA       NA       NA       NA       NA       NA   
134821       NA       NA       NA       NA       NA       NA       NA   
134822       NA       NA       NA       NA       NA       NA       NA   
134823 3.690704 3.697632 3.689425 3.685535 3.685555 3.751332       NA   
134824       NA       NA       NA       NA       NA 2.197169       NA   
134846       NA       NA       NA       NA       NA       NA       NA   
⋮      ⋮        ⋮        ⋮        ⋮        ⋮        ⋮        ⋮          
140154       NA       NA       NA       NA       NA 3.338596 NA         
140176       NA       NA       NA       NA       NA       NA NA         
140177       NA       NA       NA       NA       NA       NA NA         
140178       NA       NA       NA       NA       NA       NA NA         
140179       NA       NA       NA       NA       NA       NA NA         
140180       NA       NA       NA       NA       NA       NA NA         
140181       NA       NA       NA       NA       NA       NA NA         
140182       NA       NA       NA       NA       NA       NA NA         
140183       NA       NA       NA       NA       NA       NA NA         
140184       NA       NA       NA       NA       NA       NA NA         
140185       NA       NA       NA       NA       NA       NA NA         
140186       NA       NA       NA       NA       NA       NA NA         
140187       NA       NA       NA       NA       NA       NA NA         
140188       NA       NA       NA       NA       NA       NA NA         
140189       NA       NA       NA       NA       NA       NA NA         
140190       NA       NA       NA       NA       NA       NA NA         
140191       NA       NA       NA       NA       NA       NA NA         
140192       NA       NA       NA       NA       NA       NA NA         
140193       NA       NA       NA       NA       NA       NA NA         
140194 4.254330 4.252759 5.885289 5.887883 5.885243       NA NA         
140195       NA       NA       NA       NA       NA       NA NA         
140206       NA       NA       NA       NA       NA       NA NA         
140207       NA       NA       NA       NA       NA       NA NA  

In [239]:
write.csv(trips_RMSE_r9_d1, 'trips_RMSE_r9_d1.csv', row.names = F)